In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
import os
os.chdir('/content/drive/MyDrive/PhD/kdfl-v-4.0')

In [2]:
import numpy as np
import pandas as pd
import copy

import torch
from torch.utils.data import TensorDataset, DataLoader
from sklearn.preprocessing import MinMaxScaler

from data import fetch_dataset
from util import move_sliding_window, num_params

from model import LSTMModel
from algorithm import fedavg,fedlbskd

pd.set_option('display.max_columns', None)
pd.set_option('display.max_columns', None)
np.set_printoptions(suppress=True, floatmode='fixed')

In [3]:
if torch.cuda.is_available():
    device = torch.device("cuda")
    print('running on gpu')
else:
    device = torch.device("cpu")

running on gpu


# Parameters

In [4]:
window_size = 90 # Define window_size period and split inputs/labels\
batch_size = 1024
label_col_index = 0

# seq_len = 90  # (timestamps)
hidden_dim = 50
n_layers = 2
lr = 0.0001
output_dim = 1

#fed train params
num_local_epochs = 1
max_rounds = 100 #nb of total rounds for training


# Data Preperation

In [5]:
dataframes = fetch_dataset("./heterog")

Floor0
Floor1
Floor10
Floor11
Floor12
Floor13
Floor14
Floor15
Floor16
Floor17
Floor18
Floor19
Floor2
Floor20
Floor21
Floor22
Floor23
Floor24
Floor25
Floor26
Floor27
Floor28
Floor29
Floor3
Floor30
Floor31
Floor32
Floor33
Floor34
Floor35
Floor36
Floor37
Floor38
Floor39
Floor4
Floor40
Floor41
Floor42
Floor43
Floor44
Floor45
Floor46
Floor47
Floor48
Floor49
Floor5
Floor50
Floor51
Floor52
Floor53
Floor54
Floor55
Floor56
Floor57
Floor58
Floor59
Floor6
Floor60
Floor61
Floor62
Floor63
Floor64
Floor65
Floor66
Floor67
Floor68
Floor69
Floor7
Floor70
Floor71
Floor72
Floor73
Floor74
Floor75
Floor76
Floor77
Floor78
Floor79
Floor8
Floor80
Floor81
Floor82
Floor83
Floor84
Floor85
Floor86
Floor87
Floor88
Floor89
Floor9


In [6]:
# n_clients = len(dataframes)

In [7]:
for _, df in dataframes.items():
    print(df.columns)
    print(df.shape)
    input_dim = df.shape[1]

Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(68183, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(58618, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(46840, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(65390, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(57176, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(51707, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(47453, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
 

# LSTM model

In [8]:
lstm = LSTMModel(input_dim, hidden_dim, output_dim, n_layers)
model_type = 'LSTM'
print(lstm)
print(num_params(lstm))

LSTMModel(
  (lstm): LSTM(9, 50, num_layers=2, batch_first=True)
  (fc): Linear(in_features=50, out_features=1, bias=True)
  (tanh): Tanh()
)
32651


# FedLbsKD

# Build the training set

## 10

In [ ]:
n_clients=10

In [ ]:
train_loader = []
test_loader = []
label_scalers = []
i=0
for _, df in dataframes.items():
    if i==n_clients:
        break
    inputs_cols_indices = range(0, df.shape[1])  # use (total_demand,Year,Month,Day,Hour,Minute) columns as features
    #move the window
    inputs, labels = move_sliding_window(
        df.values,
        window_size,
        inputs_cols_indices=inputs_cols_indices,
        label_col_index=label_col_index
    )

    # Normalize the input data columns
    sc = MinMaxScaler()
    # Obtaining the scaler for the labels(usage data) so that output can be re-scaled to actual value during evaluation
    label_sc = MinMaxScaler()

    # Split data into train/test portions and combining all data into a single array
    test_portion = int(0.2 * len(inputs))

    train_x = sc.fit_transform(inputs[:-test_portion].reshape(-1, window_size * df.shape[1]))
    train_x = train_x.reshape(-1, window_size, df.shape[1])
    train_y = label_sc.fit_transform(labels[:-test_portion])

    test_x = sc.transform(inputs[-test_portion:].reshape(-1, window_size * df.shape[1]))
    test_x = test_x.reshape(-1, window_size, df.shape[1])
    test_y = label_sc.transform(labels[-test_portion:])

    # test_x.append(testx)
    # test_y.append(testy)
    label_scalers.append(label_sc)

    # pytorch data loaders
    train_data = TensorDataset(torch.from_numpy(train_x).to('cpu'), torch.from_numpy(train_y).to('cpu'))
    train_loader.append(DataLoader(train_data, batch_size=batch_size, drop_last=True))# Drop the last incomplete batch
    test_data = TensorDataset(torch.from_numpy(test_x).to('cpu'), torch.from_numpy(test_y).to('cpu'))
    test_loader.append(DataLoader(test_data, batch_size=batch_size))# Drop the last incomplete batch

    # release some memory
    del train_x, train_y
    i=i+1

(58528, 90, 9) (58528, 1)
(64807, 90, 9) (64807, 1)
(52888, 90, 9) (52888, 1)
(64836, 90, 9) (64836, 1)
(46055, 90, 9) (46055, 1)
(67334, 90, 9) (67334, 1)
(61853, 90, 9) (61853, 1)
(60219, 90, 9) (60219, 1)
(58120, 90, 9) (58120, 1)
(62212, 90, 9) (62212, 1)


In [ ]:
%%time
S = 3
lstm_lbskd = copy.deepcopy(lstm)
outputs_lbskd1, targets_lbskd1, loss_lbskd1, smape_lbskd1, mae_lbskd1, rmse_lbskd1,global_model, aggregated_logits = fedavg(
    global_model = lstm_lbskd,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = 1,
    model_type = model_type,
    device = device,
)
outputs_lbskd, targets_lbskd, loss_lbskd, smape_lbskd, mae_lbskd, rmse_lbskd = fedlbskd(
    global_model = global_model,
    aggregated_logits=aggregated_logits,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds,
    model_type = model_type,
    device = device,
    S=S
)


starting avg round 0
clients:  [0 1 2 3 4 5 6 7 8 9]
round 0, starting client 1/10, id: 0
Epoch [1/1], Train Loss: 0.05636052625874679
round 0, starting client 2/10, id: 1
Epoch [1/1], Train Loss: 0.061613677367568016
round 0, starting client 3/10, id: 2
Epoch [1/1], Train Loss: 0.0544242109739926
round 0, starting client 4/10, id: 3
Epoch [1/1], Train Loss: 0.06089315190911293
round 0, starting client 5/10, id: 4
Epoch [1/1], Train Loss: 0.052179241340075226
round 0, starting client 6/10, id: 5
Epoch [1/1], Train Loss: 0.0493053553912502
round 0, starting client 7/10, id: 6
Epoch [1/1], Train Loss: 0.0349120567746771
round 0, starting client 8/10, id: 7
Epoch [1/1], Train Loss: 0.05068078213074107
round 0, starting client 9/10, id: 8
Epoch [1/1], Train Loss: 0.05116570616761843
round 0, starting client 10/10, id: 9
Epoch [1/1], Train Loss: 0.053748948499560356
calc smape: 58.50633584449951%
MAE: 16.297602169267662
RMSE: 23.943218279099984
Average Loss:  0.0495207237861124

starting a

/usr/local/lib/python3.11/dist-packages/torch/nn/modules/loss.py:608: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.045537525580988975
round 1, starting client 2/10, id: 1
Epoch [1/1], Train Loss: 0.04950546845793725
round 1, starting client 3/10, id: 2
Epoch [1/1], Train Loss: 0.04491039392788236
round 1, starting client 4/10, id: 3
Epoch [1/1], Train Loss: 0.0497276884317398
round 1, starting client 5/10, id: 4
Epoch [1/1], Train Loss: 0.042733482856835626
round 1, starting client 6/10, id: 5
Epoch [1/1], Train Loss: 0.04219171766621563
round 1, starting client 7/10, id: 6
Epoch [1/1], Train Loss: 0.03114886205488195
round 1, starting client 8/10, id: 7
Epoch [1/1], Train Loss: 0.04261327459615595
round 1, starting client 9/10, id: 8
Epoch [1/1], Train Loss: 0.04089288815028137
round 1, starting client 10/10, id: 9
Epoch [1/1], Train Loss: 0.04401720191041628
1 [0 0 0 0 0 0 0 0 0 0]
calc smape: 59.1038941316392%
MAE: 17.194820913965046
RMSE: 22.5226676350902
Average Loss:  0.04426420706844345

starting average round 2
clients:  [0 1 2 3 4 5 6 7 8 9]
round 2, starting cli

/usr/local/lib/python3.11/dist-packages/torch/nn/modules/loss.py:608: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.03912854716181756
updating loss and weight
round 2, starting client 2/10, id: 1
Epoch [1/1], Train Loss: 0.042115875221788876
updating loss and weight
round 2, starting client 3/10, id: 2
Epoch [1/1], Train Loss: 0.03904355117460578
updating loss and weight
round 2, starting client 4/10, id: 3
Epoch [1/1], Train Loss: 0.04252198990434409
updating loss and weight
round 2, starting client 5/10, id: 4
Epoch [1/1], Train Loss: 0.037264326268008775
updating loss and weight
round 2, starting client 6/10, id: 5
Epoch [1/1], Train Loss: 0.0371216042325474
updating loss and weight
round 2, starting client 7/10, id: 6
Epoch [1/1], Train Loss: 0.0284965587585854
updating loss and weight
round 2, starting client 8/10, id: 7
Epoch [1/1], Train Loss: 0.03710071294707186
updating loss and weight
round 2, starting client 9/10, id: 8
Epoch [1/1], Train Loss: 0.0350549044708411
updating loss and weight
round 2, starting client 10/10, id: 9
Epoch [1/1], Train Loss: 0.0378879910

...

Epoch [1/1], Train Loss: 0.001999922012651546
round 97, starting client 2/10, id: 1
Epoch [1/1], Train Loss: 0.002085054630879312
round 97, starting client 3/10, id: 2
Epoch [1/1], Train Loss: 0.0019328180067354772
round 97, starting client 4/10, id: 3
Epoch [1/1], Train Loss: 0.0020784835494123406
round 97, starting client 5/10, id: 4
Epoch [1/1], Train Loss: 0.0019736777400664453
round 97, starting client 6/10, id: 5
Epoch [1/1], Train Loss: 0.002460943967050228
round 97, starting client 7/10, id: 6
Epoch [1/1], Train Loss: 0.002299809014706019
round 97, starting client 8/10, id: 7
Epoch [1/1], Train Loss: 0.002183262204275803
round 97, starting client 9/10, id: 8
Epoch [1/1], Train Loss: 0.0017393036441515307
round 97, starting client 10/10, id: 9
Epoch [1/1], Train Loss: 0.0021327014170916913
1 [0 0 0 0 0 0 0 0 0 0]
calc smape: 20.0771373873227%
MAE: 2.1456216916255513
RMSE: 5.011557202874971
Average Loss:  0.0022993259721868276

starting average round 98
clients:  [0 1 2 3 4 5 6 7

/usr/local/lib/python3.11/dist-packages/torch/nn/modules/loss.py:608: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.001994373575629046
updating loss and weight
round 98, starting client 2/10, id: 1
Epoch [1/1], Train Loss: 0.0020770164451096216
updating loss and weight
round 98, starting client 3/10, id: 2
Epoch [1/1], Train Loss: 0.0019292186991107167
updating loss and weight
round 98, starting client 4/10, id: 3
Epoch [1/1], Train Loss: 0.002066605485742912
updating loss and weight
round 98, starting client 5/10, id: 4
Epoch [1/1], Train Loss: 0.001974095103962879
updating loss and weight
round 98, starting client 6/10, id: 5
Epoch [1/1], Train Loss: 0.002449705498293042
updating loss and weight
round 98, starting client 7/10, id: 6
Epoch [1/1], Train Loss: 0.0022937110843486153
updating loss and weight
round 98, starting client 8/10, id: 7
Epoch [1/1], Train Loss: 0.002174079591566895
updating loss and weight
round 98, starting client 9/10, id: 8
Epoch [1/1], Train Loss: 0.0017322223918098542
updating loss and weight
round 98, starting client 10/10, id: 9
Epoch [1/1], T

/usr/local/lib/python3.11/dist-packages/torch/nn/modules/loss.py:608: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0019898088713590474
round 99, starting client 2/10, id: 1
Epoch [1/1], Train Loss: 0.002076037671649828
round 99, starting client 3/10, id: 2
Epoch [1/1], Train Loss: 0.0020682642949040888
round 99, starting client 4/10, id: 3
Epoch [1/1], Train Loss: 0.0020442459487821905
round 99, starting client 5/10, id: 4
Epoch [1/1], Train Loss: 0.0019508764704888953
round 99, starting client 6/10, id: 5
Epoch [1/1], Train Loss: 0.0024867886095307763
round 99, starting client 7/10, id: 6
Epoch [1/1], Train Loss: 0.0023129093436485464
round 99, starting client 8/10, id: 7
Epoch [1/1], Train Loss: 0.0021728082124064566
round 99, starting client 9/10, id: 8
Epoch [1/1], Train Loss: 0.0017579651735205616
round 99, starting client 10/10, id: 9
Epoch [1/1], Train Loss: 0.002132480483851395
1 [0 0 0 0 0 0 0 0 0 0]
calc smape: 19.95591175309245%
MAE: 2.1392561987562195
RMSE: 4.993046356061318
Average Loss:  0.0022853703917645
CPU times: user 22min 3s, sys: 6.01 s, total: 22min 

In [ ]:
loss_lbskd = np.insert(loss_lbskd, 0, loss_lbskd1)
smape_lbskd = np.insert(smape_lbskd, 0, smape_lbskd1)
mae_lbskd = np.insert(mae_lbskd, 0, mae_lbskd1)
rmse_lbskd = np.insert(mae_lbskd, 0, mae_lbskd1)

In [ ]:
np.save(f'metrics/fedlbskd_outputs_C{n_clients}.npy', np.array(outputs_lbskd, dtype=object))
np.save(f'metrics/fedlbskd_targets_C{n_clients}.npy', np.array(targets_lbskd, dtype=object))
np.save(f'metrics/fedlbskd_loss_C{n_clients}.npy', loss_lbskd)
np.save(f'metrics/fedlbskd_smape_C{n_clients}.npy', smape_lbskd)
np.save(f'metrics/fedlbskd_mae_C{n_clients}.npy', mae_lbskd)
np.save(f'metrics/fedlbskd_rmse_C{n_clients}.npy', rmse_lbskd)

## 20

In [ ]:
n_clients=20

In [ ]:
train_loader = []
test_loader = []
label_scalers = []
i=0
for _, df in dataframes.items():
    if i==n_clients:
        break
    inputs_cols_indices = range(0, df.shape[1])  # use (total_demand,Year,Month,Day,Hour,Minute) columns as features
    #move the window
    inputs, labels = move_sliding_window(
        df.values,
        window_size,
        inputs_cols_indices=inputs_cols_indices,
        label_col_index=label_col_index
    )

    # Normalize the input data columns
    sc = MinMaxScaler()
    # Obtaining the scaler for the labels(usage data) so that output can be re-scaled to actual value during evaluation
    label_sc = MinMaxScaler()

    # Split data into train/test portions and combining all data into a single array
    test_portion = int(0.2 * len(inputs))

    train_x = sc.fit_transform(inputs[:-test_portion].reshape(-1, window_size * df.shape[1]))
    train_x = train_x.reshape(-1, window_size, df.shape[1])
    train_y = label_sc.fit_transform(labels[:-test_portion])

    test_x = sc.transform(inputs[-test_portion:].reshape(-1, window_size * df.shape[1]))
    test_x = test_x.reshape(-1, window_size, df.shape[1])
    test_y = label_sc.transform(labels[-test_portion:])

    # test_x.append(testx)
    # test_y.append(testy)
    label_scalers.append(label_sc)

    # pytorch data loaders
    train_data = TensorDataset(torch.from_numpy(train_x).to('cpu'), torch.from_numpy(train_y).to('cpu'))
    train_loader.append(DataLoader(train_data, batch_size=batch_size, drop_last=True))# Drop the last incomplete batch
    test_data = TensorDataset(torch.from_numpy(test_x).to('cpu'), torch.from_numpy(test_y).to('cpu'))
    test_loader.append(DataLoader(test_data, batch_size=batch_size))# Drop the last incomplete batch

    # release some memory
    del train_x, train_y
    i=i+1
input_dim = next(iter(train_loader[0]))[0].shape[2]  # 22

(58528, 90, 9) (58528, 1)
(64807, 90, 9) (64807, 1)
(52888, 90, 9) (52888, 1)
(64836, 90, 9) (64836, 1)
(46055, 90, 9) (46055, 1)
(67334, 90, 9) (67334, 1)
(61853, 90, 9) (61853, 1)
(60219, 90, 9) (60219, 1)
(58120, 90, 9) (58120, 1)
(62212, 90, 9) (62212, 1)
(65910, 90, 9) (65910, 1)
(49050, 90, 9) (49050, 1)
(61800, 90, 9) (61800, 1)
(68093, 90, 9) (68093, 1)
(68901, 90, 9) (68901, 1)
(49996, 90, 9) (49996, 1)
(65300, 90, 9) (65300, 1)
(47544, 90, 9) (47544, 1)
(57086, 90, 9) (57086, 1)
(55024, 90, 9) (55024, 1)


In [ ]:
%%time
S = 3
lstm_lbskd = copy.deepcopy(lstm)
outputs_lbskd1, targets_lbskd1, loss_lbskd1, smape_lbskd1, mae_lbskd1, rmse_lbskd1,global_model, aggregated_logits = fedavg(
    global_model = lstm_lbskd,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = 1,
    model_type = model_type,
    device = device,
)
outputs_lbskd, targets_lbskd, loss_lbskd, smape_lbskd, mae_lbskd, rmse_lbskd = fedlbskd(
    global_model = global_model,
    aggregated_logits=aggregated_logits,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,

    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds-1,
    model_type = model_type,
    device = device,
    S=S
)


starting avg round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19]
round 0, starting client 1/20, id: 0
Epoch [1/1], Train Loss: 0.05636052625874679
round 0, starting client 2/20, id: 1
Epoch [1/1], Train Loss: 0.061613677367568016
round 0, starting client 3/20, id: 2
Epoch [1/1], Train Loss: 0.0544242109739926
round 0, starting client 4/20, id: 3
Epoch [1/1], Train Loss: 0.06089315190911293
round 0, starting client 5/20, id: 4
Epoch [1/1], Train Loss: 0.052179241340075226
round 0, starting client 6/20, id: 5
Epoch [1/1], Train Loss: 0.0493053553912502
round 0, starting client 7/20, id: 6
Epoch [1/1], Train Loss: 0.0349120567746771
round 0, starting client 8/20, id: 7
Epoch [1/1], Train Loss: 0.05068078213074107
round 0, starting client 9/20, id: 8
Epoch [1/1], Train Loss: 0.05116570616761843
round 0, starting client 10/20, id: 9
Epoch [1/1], Train Loss: 0.053748948499560356
round 0, starting client 11/20, id: 10
Epoch [1/1], Train Loss: 0.059690888386731054


/usr/local/lib/python3.11/dist-packages/torch/nn/modules/loss.py:608: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.045731395131184
round 1, starting client 2/20, id: 1
Epoch [1/1], Train Loss: 0.04970882087945938
round 1, starting client 3/20, id: 2
Epoch [1/1], Train Loss: 0.04509839124795868
round 1, starting client 4/20, id: 3
Epoch [1/1], Train Loss: 0.04993683494627473
round 1, starting client 5/20, id: 4
Epoch [1/1], Train Loss: 0.04291507128093923
round 1, starting client 6/20, id: 5
Epoch [1/1], Train Loss: 0.0423729926204452
round 1, starting client 7/20, id: 6
Epoch [1/1], Train Loss: 0.03129764343611895
round 1, starting client 8/20, id: 7
Epoch [1/1], Train Loss: 0.042798709203588206
round 1, starting client 9/20, id: 8
Epoch [1/1], Train Loss: 0.04106637429859902
round 1, starting client 10/20, id: 9
Epoch [1/1], Train Loss: 0.04419457893042514
round 1, starting client 11/20, id: 10
Epoch [1/1], Train Loss: 0.04857911534753499
round 1, starting client 12/20, id: 11
Epoch [1/1], Train Loss: 0.034982722987862015
round 1, starting client 13/20, id: 12
Epoch [1/1

/usr/local/lib/python3.11/dist-packages/torch/nn/modules/loss.py:608: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.03970959836410152
updating loss and weight
round 2, starting client 2/20, id: 1
Epoch [1/1], Train Loss: 0.04269357413053511
updating loss and weight
round 2, starting client 3/20, id: 2
Epoch [1/1], Train Loss: 0.03961665269623443
updating loss and weight
round 2, starting client 4/20, id: 3
Epoch [1/1], Train Loss: 0.043164189532399165
updating loss and weight
round 2, starting client 5/20, id: 4
Epoch [1/1], Train Loss: 0.037786820424454554
updating loss and weight
round 2, starting client 6/20, id: 5
Epoch [1/1], Train Loss: 0.03768595673430424
updating loss and weight
round 2, starting client 7/20, id: 6
Epoch [1/1], Train Loss: 0.02901202750702699
updating loss and weight
round 2, starting client 8/20, id: 7
Epoch [1/1], Train Loss: 0.037677510978376606
updating loss and weight
round 2, starting client 9/20, id: 8
Epoch [1/1], Train Loss: 0.035574862899051776
updating loss and weight
round 2, starting client 10/20, id: 9
Epoch [1/1], Train Loss: 0.03841

...

Epoch [1/1], Train Loss: 0.0021003944184889815
round 96, starting client 2/20, id: 1
Epoch [1/1], Train Loss: 0.0021893104835180558
round 96, starting client 3/20, id: 2
Epoch [1/1], Train Loss: 0.002026980803859216
round 96, starting client 4/20, id: 3
Epoch [1/1], Train Loss: 0.002158411353593693
round 96, starting client 5/20, id: 4
Epoch [1/1], Train Loss: 0.0020885020660768665
round 96, starting client 6/20, id: 5
Epoch [1/1], Train Loss: 0.00260428611923439
round 96, starting client 7/20, id: 6
Epoch [1/1], Train Loss: 0.0023669485684270817
round 96, starting client 8/20, id: 7
Epoch [1/1], Train Loss: 0.002303118462069951
round 96, starting client 9/20, id: 8
Epoch [1/1], Train Loss: 0.0021027848370269767
round 96, starting client 10/20, id: 9
Epoch [1/1], Train Loss: 0.0022098735789768398
round 96, starting client 11/20, id: 10
Epoch [1/1], Train Loss: 0.002215856197746653
round 96, starting client 12/20, id: 11
Epoch [1/1], Train Loss: 0.0021701130011167963
round 96, starting 

/usr/local/lib/python3.11/dist-packages/torch/nn/modules/loss.py:608: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.002092816786737078
round 97, starting client 2/20, id: 1
Epoch [1/1], Train Loss: 0.002183313610148616
round 97, starting client 3/20, id: 2
Epoch [1/1], Train Loss: 0.0020154454161855962
round 97, starting client 4/20, id: 3
Epoch [1/1], Train Loss: 0.0021786899352446197
round 97, starting client 5/20, id: 4
Epoch [1/1], Train Loss: 0.002049858672294899
round 97, starting client 6/20, id: 5
Epoch [1/1], Train Loss: 0.002589110996968185
round 97, starting client 7/20, id: 6
Epoch [1/1], Train Loss: 0.002369371615107715
round 97, starting client 8/20, id: 7
Epoch [1/1], Train Loss: 0.0023087295827436
round 97, starting client 9/20, id: 8
Epoch [1/1], Train Loss: 0.0017348142127351217
round 97, starting client 10/20, id: 9
Epoch [1/1], Train Loss: 0.002210671642387752
round 97, starting client 11/20, id: 10
Epoch [1/1], Train Loss: 0.0022179278038332566
round 97, starting client 12/20, id: 11
Epoch [1/1], Train Loss: 0.0021746348418099307
round 97, starting cli

/usr/local/lib/python3.11/dist-packages/torch/nn/modules/loss.py:608: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0020897071265305084
updating loss and weight
round 98, starting client 2/20, id: 1
Epoch [1/1], Train Loss: 0.0021807889896444978
updating loss and weight
round 98, starting client 3/20, id: 2
Epoch [1/1], Train Loss: 0.00201772632809901
updating loss and weight
round 98, starting client 4/20, id: 3
Epoch [1/1], Train Loss: 0.002144659255864099
updating loss and weight
round 98, starting client 5/20, id: 4
Epoch [1/1], Train Loss: 0.00204414914811163
updating loss and weight
round 98, starting client 6/20, id: 5
Epoch [1/1], Train Loss: 0.002578765714693313
updating loss and weight
round 98, starting client 7/20, id: 6
Epoch [1/1], Train Loss: 0.0023618064236264518
updating loss and weight
round 98, starting client 8/20, id: 7
Epoch [1/1], Train Loss: 0.002297683331639843
updating loss and weight
round 98, starting client 9/20, id: 8
Epoch [1/1], Train Loss: 0.0017305240843496809
updating loss and weight
round 98, starting client 10/20, id: 9
Epoch [1/1], Tra

In [ ]:
loss_lbskd = np.insert(loss_lbskd, 0, loss_lbskd1)
smape_lbskd = np.insert(smape_lbskd, 0, smape_lbskd1)
mae_lbskd = np.insert(mae_lbskd, 0, mae_lbskd1)
rmse_lbskd = np.insert(mae_lbskd, 0, mae_lbskd1)

In [ ]:
np.save(f'metrics/fedlbskd_outputs_C{n_clients}.npy', np.array(outputs_lbskd, dtype=object))
np.save(f'metrics/fedlbskd_targets_C{n_clients}.npy', np.array(targets_lbskd, dtype=object))
np.save(f'metrics/fedlbskd_loss_C{n_clients}.npy', loss_lbskd)
np.save(f'metrics/fedlbskd_smape_C{n_clients}.npy', smape_lbskd)
np.save(f'metrics/fedlbskd_mae_C{n_clients}.npy', mae_lbskd)
np.save(f'metrics/fedlbskd_rmse_C{n_clients}.npy', rmse_lbskd)

## 30

In [14]:
n_clients=30

In [16]:
train_loader = []
test_loader = []
label_scalers = []
i=0
for _, df in dataframes.items():
    if i==n_clients:
        break
    inputs_cols_indices = range(0, df.shape[1])  # use (total_demand,Year,Month,Day,Hour,Minute) columns as features
    #move the window
    inputs, labels = move_sliding_window(
        df.values,
        window_size,
        inputs_cols_indices=inputs_cols_indices,
        label_col_index=label_col_index
    )

    # Normalize the input data columns
    sc = MinMaxScaler()
    # Obtaining the scaler for the labels(usage data) so that output can be re-scaled to actual value during evaluation
    label_sc = MinMaxScaler()

    # Split data into train/test portions and combining all data into a single array
    test_portion = int(0.2 * len(inputs))

    train_x = sc.fit_transform(inputs[:-test_portion].reshape(-1, window_size * df.shape[1]))
    train_x = train_x.reshape(-1, window_size, df.shape[1])
    train_y = label_sc.fit_transform(labels[:-test_portion])

    test_x = sc.transform(inputs[-test_portion:].reshape(-1, window_size * df.shape[1]))
    test_x = test_x.reshape(-1, window_size, df.shape[1])
    test_y = label_sc.transform(labels[-test_portion:])

    # test_x.append(testx)
    # test_y.append(testy)
    label_scalers.append(label_sc)

    # pytorch data loaders
    train_data = TensorDataset(torch.from_numpy(train_x).to(device), torch.from_numpy(train_y).to(device))
    train_loader.append(DataLoader(train_data, batch_size=batch_size, drop_last=True))# Drop the last incomplete batch
    test_data = TensorDataset(torch.from_numpy(test_x).to(device), torch.from_numpy(test_y).to(device))
    test_loader.append(DataLoader(test_data, batch_size=batch_size))# Drop the last incomplete batch

    # release some memory
    del train_x, train_y
    i=i+1
input_dim = next(iter(train_loader[0]))[0].shape[2]  # 22

(58528, 90, 9) (58528, 1)
(64807, 90, 9) (64807, 1)
(52888, 90, 9) (52888, 1)
(64836, 90, 9) (64836, 1)
(46055, 90, 9) (46055, 1)
(67334, 90, 9) (67334, 1)
(61853, 90, 9) (61853, 1)
(60219, 90, 9) (60219, 1)
(58120, 90, 9) (58120, 1)
(62212, 90, 9) (62212, 1)
(65910, 90, 9) (65910, 1)
(49050, 90, 9) (49050, 1)
(61800, 90, 9) (61800, 1)
(68093, 90, 9) (68093, 1)
(68901, 90, 9) (68901, 1)
(49996, 90, 9) (49996, 1)
(65300, 90, 9) (65300, 1)
(47544, 90, 9) (47544, 1)
(57086, 90, 9) (57086, 1)
(55024, 90, 9) (55024, 1)
(56491, 90, 9) (56491, 1)
(69578, 90, 9) (69578, 1)
(72217, 90, 9) (72217, 1)
(47363, 90, 9) (47363, 1)
(67302, 90, 9) (67302, 1)
(62003, 90, 9) (62003, 1)
(46750, 90, 9) (46750, 1)
(69858, 90, 9) (69858, 1)
(51617, 90, 9) (51617, 1)
(63049, 90, 9) (63049, 1)


In [17]:
%%time
S = 3
lstm_lbskd = copy.deepcopy(lstm)
outputs_lbskd1, targets_lbskd1, loss_lbskd1, smape_lbskd1, mae_lbskd1, rmse_lbskd1,global_model, aggregated_logits = fedavg(
    global_model = lstm_lbskd,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = 1,
    model_type = model_type,
    device = device,
)
outputs_lbskd, targets_lbskd, loss_lbskd, smape_lbskd, mae_lbskd, rmse_lbskd = fedlbskd(
    global_model = global_model,
    aggregated_logits=aggregated_logits,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,

    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds-1,
    model_type = model_type,
    device = device,
    S=S
)


starting avg round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29]
round 0, starting client 1/30, id: 0
Epoch [1/1], Train Loss: 0.05066361632198097
round 0, starting client 2/30, id: 1
Epoch [1/1], Train Loss: 0.055368726029992106
round 0, starting client 3/30, id: 2
Epoch [1/1], Train Loss: 0.04973255393163461
round 0, starting client 4/30, id: 3
Epoch [1/1], Train Loss: 0.055162621736526495
round 0, starting client 5/30, id: 4
Epoch [1/1], Train Loss: 0.0474983286112547
round 0, starting client 6/30, id: 5
Epoch [1/1], Train Loss: 0.046075736853079155
round 0, starting client 7/30, id: 6
Epoch [1/1], Train Loss: 0.0338230119086802
round 0, starting client 8/30, id: 7
Epoch [1/1], Train Loss: 0.04684939730833186
round 0, starting client 9/30, id: 8
Epoch [1/1], Train Loss: 0.04577606846061017
round 0, starting client 10/30, id: 9
Epoch [1/1], Train Loss: 0.04861316542762022
round 0, starting client 11/30, id: 10
Epoch [1/1], T

/usr/local/lib/python3.11/dist-packages/torch/nn/modules/loss.py:608: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.04407593222955862
round 1, starting client 2/30, id: 1
Epoch [1/1], Train Loss: 0.047602967172861096
round 1, starting client 3/30, id: 2
Epoch [1/1], Train Loss: 0.04385386802619551
round 1, starting client 4/30, id: 3
Epoch [1/1], Train Loss: 0.047992396801710135
round 1, starting client 5/30, id: 4
Epoch [1/1], Train Loss: 0.04192303791642189
round 1, starting client 6/30, id: 5
Epoch [1/1], Train Loss: 0.04127415266031256
round 1, starting client 7/30, id: 6
Epoch [1/1], Train Loss: 0.03156135466027385
round 1, starting client 8/30, id: 7
Epoch [1/1], Train Loss: 0.04147832472115122
round 1, starting client 9/30, id: 8
Epoch [1/1], Train Loss: 0.039671933030088743
round 1, starting client 10/30, id: 9
Epoch [1/1], Train Loss: 0.04239730350673199
round 1, starting client 11/30, id: 10
Epoch [1/1], Train Loss: 0.04643205370680958
round 1, starting client 12/30, id: 11
Epoch [1/1], Train Loss: 0.03431473863556197
round 1, starting client 13/30, id: 12
Epoch 

/usr/local/lib/python3.11/dist-packages/torch/nn/modules/loss.py:608: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.037054249520103145
updating loss and weight
round 2, starting client 2/30, id: 1
Epoch [1/1], Train Loss: 0.03982464998960494
updating loss and weight
round 2, starting client 3/30, id: 2
Epoch [1/1], Train Loss: 0.037195874923249585
updating loss and weight
round 2, starting client 4/30, id: 3
Epoch [1/1], Train Loss: 0.039896078109741225
updating loss and weight
round 2, starting client 5/30, id: 4
Epoch [1/1], Train Loss: 0.03566180249410016
updating loss and weight
round 2, starting client 6/30, id: 5
Epoch [1/1], Train Loss: 0.03498708682421309
updating loss and weight
round 2, starting client 7/30, id: 6
Epoch [1/1], Train Loss: 0.027463134378194812
updating loss and weight
round 2, starting client 8/30, id: 7
Epoch [1/1], Train Loss: 0.034950907005274555
updating loss and weight
round 2, starting client 9/30, id: 8
Epoch [1/1], Train Loss: 0.03346512301100626
updating loss and weight
round 2, starting client 10/30, id: 9
Epoch [1/1], Train Loss: 0.0354

...

Epoch [1/1], Train Loss: 0.002082516849299686
round 96, starting client 2/30, id: 1
Epoch [1/1], Train Loss: 0.0021701875946018847
round 96, starting client 3/30, id: 2
Epoch [1/1], Train Loss: 0.0020354739049585854
round 96, starting client 4/30, id: 3
Epoch [1/1], Train Loss: 0.002151604630053044
round 96, starting client 5/30, id: 4
Epoch [1/1], Train Loss: 0.0020487234827929303
round 96, starting client 6/30, id: 5
Epoch [1/1], Train Loss: 0.002669463778147475
round 96, starting client 7/30, id: 6
Epoch [1/1], Train Loss: 0.0023243508670323823
round 96, starting client 8/30, id: 7
Epoch [1/1], Train Loss: 0.002291273961012113
round 96, starting client 9/30, id: 8
Epoch [1/1], Train Loss: 0.001984804789794402
round 96, starting client 10/30, id: 9
Epoch [1/1], Train Loss: 0.002190786156764564
round 96, starting client 11/30, id: 10
Epoch [1/1], Train Loss: 0.0022174319727163694
round 96, starting client 12/30, id: 11
Epoch [1/1], Train Loss: 0.0021767366806192223
round 96, starting 

/usr/local/lib/python3.11/dist-packages/torch/nn/modules/loss.py:608: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0020931084588583972
round 97, starting client 2/30, id: 1
Epoch [1/1], Train Loss: 0.0021810160443419594
round 97, starting client 3/30, id: 2
Epoch [1/1], Train Loss: 0.0020346748294797156
round 97, starting client 4/30, id: 3
Epoch [1/1], Train Loss: 0.0021488964476156984
round 97, starting client 5/30, id: 4
Epoch [1/1], Train Loss: 0.002031823897933854
round 97, starting client 6/30, id: 5
Epoch [1/1], Train Loss: 0.002606441882492688
round 97, starting client 7/30, id: 6
Epoch [1/1], Train Loss: 0.0023410674111801204
round 97, starting client 8/30, id: 7
Epoch [1/1], Train Loss: 0.002279119367929215
round 97, starting client 9/30, id: 8
Epoch [1/1], Train Loss: 0.0017905352857067358
round 97, starting client 10/30, id: 9
Epoch [1/1], Train Loss: 0.0021769153827335685
round 97, starting client 11/30, id: 10
Epoch [1/1], Train Loss: 0.002218263006915211
round 97, starting client 12/30, id: 11
Epoch [1/1], Train Loss: 0.0021892261682200783
round 97, startin

/usr/local/lib/python3.11/dist-packages/torch/nn/modules/loss.py:608: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0020887252460751265
updating loss and weight
round 98, starting client 2/30, id: 1
Epoch [1/1], Train Loss: 0.0021755132457474246
updating loss and weight
round 98, starting client 3/30, id: 2
Epoch [1/1], Train Loss: 0.0020335294553305867
updating loss and weight
round 98, starting client 4/30, id: 3
Epoch [1/1], Train Loss: 0.002141424624715
updating loss and weight
round 98, starting client 5/30, id: 4
Epoch [1/1], Train Loss: 0.0020250981191306237
updating loss and weight
round 98, starting client 6/30, id: 5
Epoch [1/1], Train Loss: 0.0025946066687958175
updating loss and weight
round 98, starting client 7/30, id: 6
Epoch [1/1], Train Loss: 0.0023337032156026303
updating loss and weight
round 98, starting client 8/30, id: 7
Epoch [1/1], Train Loss: 0.0022695193926684882
updating loss and weight
round 98, starting client 9/30, id: 8
Epoch [1/1], Train Loss: 0.0017880551717502791
updating loss and weight
round 98, starting client 10/30, id: 9
Epoch [1/1], 

In [18]:
loss_lbskd = np.insert(loss_lbskd, 0, loss_lbskd1)
smape_lbskd = np.insert(smape_lbskd, 0, smape_lbskd1)
mae_lbskd = np.insert(mae_lbskd, 0, mae_lbskd1)
rmse_lbskd = np.insert(mae_lbskd, 0, mae_lbskd1)

In [19]:
np.save(f'metrics/fedlbskd_outputs_C{n_clients}.npy', np.array(outputs_lbskd, dtype=object))
np.save(f'metrics/fedlbskd_targets_C{n_clients}.npy', np.array(targets_lbskd, dtype=object))
np.save(f'metrics/fedlbskd_loss_C{n_clients}.npy', loss_lbskd)
np.save(f'metrics/fedlbskd_smape_C{n_clients}.npy', smape_lbskd)
np.save(f'metrics/fedlbskd_mae_C{n_clients}.npy', mae_lbskd)
np.save(f'metrics/fedlbskd_rmse_C{n_clients}.npy', rmse_lbskd)

## 40

In [8]:
n_clients=40

In [9]:
train_loader = []
test_loader = []
label_scalers = []
i=0
for _, df in dataframes.items():
    if i==n_clients:
        break
    inputs_cols_indices = range(0, df.shape[1])  # use (total_demand,Year,Month,Day,Hour,Minute) columns as features
    #move the window
    inputs, labels = move_sliding_window(
        df.values,
        window_size,
        inputs_cols_indices=inputs_cols_indices,
        label_col_index=label_col_index
    )

    # Normalize the input data columns
    sc = MinMaxScaler()
    # Obtaining the scaler for the labels(usage data) so that output can be re-scaled to actual value during evaluation
    label_sc = MinMaxScaler()

    # Split data into train/test portions and combining all data into a single array
    test_portion = int(0.2 * len(inputs))

    train_x = sc.fit_transform(inputs[:-test_portion].reshape(-1, window_size * df.shape[1]))
    train_x = train_x.reshape(-1, window_size, df.shape[1])
    train_y = label_sc.fit_transform(labels[:-test_portion])

    test_x = sc.transform(inputs[-test_portion:].reshape(-1, window_size * df.shape[1]))
    test_x = test_x.reshape(-1, window_size, df.shape[1])
    test_y = label_sc.transform(labels[-test_portion:])

    # test_x.append(testx)
    # test_y.append(testy)
    label_scalers.append(label_sc)

    # pytorch data loaders
    train_data = TensorDataset(torch.from_numpy(train_x).to("cpu"), torch.from_numpy(train_y).to("cpu"))
    train_loader.append(DataLoader(train_data, batch_size=batch_size, drop_last=True))# Drop the last incomplete batch
    test_data = TensorDataset(torch.from_numpy(test_x).to("cpu"), torch.from_numpy(test_y).to("cpu"))
    test_loader.append(DataLoader(test_data, batch_size=batch_size))# Drop the last incomplete batch

    # release some memory
    del train_x, train_y
    i=i+1
input_dim = next(iter(train_loader[0]))[0].shape[2]  # 22

(68093, 90, 9) (68093, 1)
(58528, 90, 9) (58528, 1)
(46750, 90, 9) (46750, 1)
(65300, 90, 9) (65300, 1)
(57086, 90, 9) (57086, 1)
(51617, 90, 9) (51617, 1)
(47363, 90, 9) (47363, 1)
(68901, 90, 9) (68901, 1)
(67168, 90, 9) (67168, 1)
(69578, 90, 9) (69578, 1)
(62003, 90, 9) (62003, 1)
(49050, 90, 9) (49050, 1)
(61853, 90, 9) (61853, 1)
(69521, 90, 9) (69521, 1)
(67302, 90, 9) (67302, 1)
(72217, 90, 9) (72217, 1)
(46055, 90, 9) (46055, 1)
(57157, 90, 9) (57157, 1)
(64807, 90, 9) (64807, 1)
(66845, 90, 9) (66845, 1)
(61800, 90, 9) (61800, 1)
(55024, 90, 9) (55024, 1)
(65910, 90, 9) (65910, 1)
(49996, 90, 9) (49996, 1)
(63049, 90, 9) (63049, 1)
(64836, 90, 9) (64836, 1)
(64007, 90, 9) (64007, 1)
(69858, 90, 9) (69858, 1)
(56491, 90, 9) (56491, 1)
(65359, 90, 9) (65359, 1)
(61733, 90, 9) (61733, 1)
(66320, 90, 9) (66320, 1)
(61236, 90, 9) (61236, 1)
(71305, 90, 9) (71305, 1)
(52888, 90, 9) (52888, 1)
(58160, 90, 9) (58160, 1)
(70972, 90, 9) (70972, 1)
(61987, 90, 9) (61987, 1)
(43972, 90, 

In [10]:
%%time
S = 3
lstm_lbskd = copy.deepcopy(lstm)
outputs_lbskd1, targets_lbskd1, loss_lbskd1, smape_lbskd1, mae_lbskd1, rmse_lbskd1,global_model, aggregated_logits = fedavg(
    global_model = lstm_lbskd,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = 1,
    model_type = model_type,
    device = device,
)
outputs_lbskd, targets_lbskd, loss_lbskd, smape_lbskd, mae_lbskd, rmse_lbskd = fedlbskd(
    global_model = global_model,
    aggregated_logits=aggregated_logits,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,

    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds-1,
    model_type = model_type,
    device = device,
    S=S
)


starting avg round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39]
round 0, starting client 1/40, id: 0
Epoch [1/1], Train Loss: 0.0889986383746255
round 0, starting client 2/40, id: 1
Epoch [1/1], Train Loss: 0.07721613488263554
round 0, starting client 3/40, id: 2
Epoch [1/1], Train Loss: 0.06492493125713532
round 0, starting client 4/40, id: 3
Epoch [1/1], Train Loss: 0.06847643625794672
round 0, starting client 5/40, id: 4
Epoch [1/1], Train Loss: 0.08233322702686895
round 0, starting client 6/40, id: 5
Epoch [1/1], Train Loss: 0.07239128379151223
round 0, starting client 7/40, id: 6
Epoch [1/1], Train Loss: 0.0892609113172905
round 0, starting client 8/40, id: 7
Epoch [1/1], Train Loss: 0.07425101656677587
round 0, starting client 9/40, id: 8
Epoch [1/1], Train Loss: 0.07519693504302546
round 0, starting client 10/40, id: 9
Epoch [1/1], Train Loss: 0.06524264572740154
round 0, starting client 1

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.06337242847624817
round 1, starting client 2/40, id: 1
Epoch [1/1], Train Loss: 0.052943203598260886
round 1, starting client 3/40, id: 2
Epoch [1/1], Train Loss: 0.044970183814358376
round 1, starting client 4/40, id: 3
Epoch [1/1], Train Loss: 0.05005646529881394
round 1, starting client 5/40, id: 4
Epoch [1/1], Train Loss: 0.05700045328756625
round 1, starting client 6/40, id: 5
Epoch [1/1], Train Loss: 0.050768912839703265
round 1, starting client 7/40, id: 6
Epoch [1/1], Train Loss: 0.06221726219597702
round 1, starting client 8/40, id: 7
Epoch [1/1], Train Loss: 0.04960296127312588
round 1, starting client 9/40, id: 8
Epoch [1/1], Train Loss: 0.05470342020719098
round 1, starting client 10/40, id: 9
Epoch [1/1], Train Loss: 0.0450246069856264
round 1, starting client 11/40, id: 10
Epoch [1/1], Train Loss: 0.06338250807796915
round 1, starting client 12/40, id: 11
Epoch [1/1], Train Loss: 0.03951622589834427
round 1, starting client 13/40, id: 12
Epoch [

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.050574513187385955
updating loss and weight
round 2, starting client 2/40, id: 1
Epoch [1/1], Train Loss: 0.0423679794702265
updating loss and weight
round 2, starting client 3/40, id: 2
Epoch [1/1], Train Loss: 0.038093476375151016
updating loss and weight
round 2, starting client 4/40, id: 3
Epoch [1/1], Train Loss: 0.042896416257409496
updating loss and weight
round 2, starting client 5/40, id: 4
Epoch [1/1], Train Loss: 0.04538313460282301
updating loss and weight
round 2, starting client 6/40, id: 5
Epoch [1/1], Train Loss: 0.041790499305352564
updating loss and weight
round 2, starting client 7/40, id: 6
Epoch [1/1], Train Loss: 0.04866740726739972
updating loss and weight
round 2, starting client 8/40, id: 7
Epoch [1/1], Train Loss: 0.03895517948241729
updating loss and weight
round 2, starting client 9/40, id: 8
Epoch [1/1], Train Loss: 0.04587905083854612
updating loss and weight
round 2, starting client 10/40, id: 9
Epoch [1/1], Train Loss: 0.036452

...

Epoch [1/1], Train Loss: 0.0020182949440325343
round 96, starting client 2/40, id: 1
Epoch [1/1], Train Loss: 0.0019103438412356702
round 96, starting client 3/40, id: 2
Epoch [1/1], Train Loss: 0.0023387174134970536
round 96, starting client 4/40, id: 3
Epoch [1/1], Train Loss: 0.002299480231515333
round 96, starting client 5/40, id: 4
Epoch [1/1], Train Loss: 0.0020216926323800267
round 96, starting client 6/40, id: 5
Epoch [1/1], Train Loss: 0.001974811043328373
round 96, starting client 7/40, id: 6
Epoch [1/1], Train Loss: 0.0018760971127178624
round 96, starting client 8/40, id: 7
Epoch [1/1], Train Loss: 0.0035761908500648596
round 96, starting client 9/40, id: 8
Epoch [1/1], Train Loss: 0.0026115887605835894
round 96, starting client 10/40, id: 9
Epoch [1/1], Train Loss: 0.0019080435336541598
round 96, starting client 11/40, id: 10
Epoch [1/1], Train Loss: 0.0021418940292884754
round 96, starting client 12/40, id: 11
Epoch [1/1], Train Loss: 0.0019735494922650484
round 96, start

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.00180411061825547
round 97, starting client 2/40, id: 1
Epoch [1/1], Train Loss: 0.0018792306836177073
round 97, starting client 3/40, id: 2
Epoch [1/1], Train Loss: 0.0022029389704888067
round 97, starting client 4/40, id: 3
Epoch [1/1], Train Loss: 0.002265229309890784
round 97, starting client 5/40, id: 4
Epoch [1/1], Train Loss: 0.00202372815428217
round 97, starting client 6/40, id: 5
Epoch [1/1], Train Loss: 0.0019851705314067663
round 97, starting client 7/40, id: 6
Epoch [1/1], Train Loss: 0.001879175171583287
round 97, starting client 8/40, id: 7
Epoch [1/1], Train Loss: 0.0014370364715775722
round 97, starting client 9/40, id: 8
Epoch [1/1], Train Loss: 0.0025325518822333273
round 97, starting client 10/40, id: 9
Epoch [1/1], Train Loss: 0.00187782744210886
round 97, starting client 11/40, id: 10
Epoch [1/1], Train Loss: 0.002128043693422418
round 97, starting client 12/40, id: 11
Epoch [1/1], Train Loss: 0.0019774807519034334
round 97, starting cli

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.001800575980011655
updating loss and weight
round 98, starting client 2/40, id: 1
Epoch [1/1], Train Loss: 0.0018733548259155619
updating loss and weight
round 98, starting client 3/40, id: 2
Epoch [1/1], Train Loss: 0.0021869805124070905
updating loss and weight
round 98, starting client 4/40, id: 3
Epoch [1/1], Train Loss: 0.002256969550359702
updating loss and weight
round 98, starting client 5/40, id: 4
Epoch [1/1], Train Loss: 0.0020192045194562525
updating loss and weight
round 98, starting client 6/40, id: 5
Epoch [1/1], Train Loss: 0.0019786836477578623
updating loss and weight
round 98, starting client 7/40, id: 6
Epoch [1/1], Train Loss: 0.0018736076717441148
updating loss and weight
round 98, starting client 8/40, id: 7
Epoch [1/1], Train Loss: 0.0014365147359950362
updating loss and weight
round 98, starting client 9/40, id: 8
Epoch [1/1], Train Loss: 0.002525385733371457
updating loss and weight
round 98, starting client 10/40, id: 9
Epoch [1/1],

In [11]:
loss_lbskd = np.insert(loss_lbskd, 0, loss_lbskd1)
smape_lbskd = np.insert(smape_lbskd, 0, smape_lbskd1)
mae_lbskd = np.insert(mae_lbskd, 0, mae_lbskd1)
rmse_lbskd = np.insert(mae_lbskd, 0, mae_lbskd1)

In [12]:
np.save(f'metrics/fedlbskd_outputs_C{n_clients}.npy', np.array(outputs_lbskd, dtype=object))
np.save(f'metrics/fedlbskd_targets_C{n_clients}.npy', np.array(targets_lbskd, dtype=object))
np.save(f'metrics/fedlbskd_loss_C{n_clients}.npy', loss_lbskd)
np.save(f'metrics/fedlbskd_smape_C{n_clients}.npy', smape_lbskd)
np.save(f'metrics/fedlbskd_mae_C{n_clients}.npy', mae_lbskd)
np.save(f'metrics/fedlbskd_rmse_C{n_clients}.npy', rmse_lbskd)

## 50

In [13]:
n_clients=50

In [14]:
train_loader = []
test_loader = []
label_scalers = []
i=0
for _, df in dataframes.items():
    if i==n_clients:
        break
    inputs_cols_indices = range(0, df.shape[1])  # use (total_demand,Year,Month,Day,Hour,Minute) columns as features
    #move the window
    inputs, labels = move_sliding_window(
        df.values,
        window_size,
        inputs_cols_indices=inputs_cols_indices,
        label_col_index=label_col_index
    )

    # Normalize the input data columns
    sc = MinMaxScaler()
    # Obtaining the scaler for the labels(usage data) so that output can be re-scaled to actual value during evaluation
    label_sc = MinMaxScaler()

    # Split data into train/test portions and combining all data into a single array
    test_portion = int(0.2 * len(inputs))

    train_x = sc.fit_transform(inputs[:-test_portion].reshape(-1, window_size * df.shape[1]))
    train_x = train_x.reshape(-1, window_size, df.shape[1])
    train_y = label_sc.fit_transform(labels[:-test_portion])

    test_x = sc.transform(inputs[-test_portion:].reshape(-1, window_size * df.shape[1]))
    test_x = test_x.reshape(-1, window_size, df.shape[1])
    test_y = label_sc.transform(labels[-test_portion:])

    # test_x.append(testx)
    # test_y.append(testy)
    label_scalers.append(label_sc)

    # pytorch data loaders
    train_data = TensorDataset(torch.from_numpy(train_x).to('cpu'), torch.from_numpy(train_y).to('cpu'))
    train_loader.append(DataLoader(train_data, batch_size=batch_size, drop_last=True))# Drop the last incomplete batch
    test_data = TensorDataset(torch.from_numpy(test_x).to('cpu'), torch.from_numpy(test_y).to('cpu'))
    test_loader.append(DataLoader(test_data, batch_size=batch_size))# Drop the last incomplete batch

    # release some memory
    del train_x, train_y
    i=i+1
input_dim = next(iter(train_loader[0]))[0].shape[2]  # 22

(68093, 90, 9) (68093, 1)
(58528, 90, 9) (58528, 1)
(46750, 90, 9) (46750, 1)
(65300, 90, 9) (65300, 1)
(57086, 90, 9) (57086, 1)
(51617, 90, 9) (51617, 1)
(47363, 90, 9) (47363, 1)
(68901, 90, 9) (68901, 1)
(67168, 90, 9) (67168, 1)
(69578, 90, 9) (69578, 1)
(62003, 90, 9) (62003, 1)
(49050, 90, 9) (49050, 1)
(61853, 90, 9) (61853, 1)
(69521, 90, 9) (69521, 1)
(67302, 90, 9) (67302, 1)
(72217, 90, 9) (72217, 1)
(46055, 90, 9) (46055, 1)
(57157, 90, 9) (57157, 1)
(64807, 90, 9) (64807, 1)
(66845, 90, 9) (66845, 1)
(61800, 90, 9) (61800, 1)
(55024, 90, 9) (55024, 1)
(65910, 90, 9) (65910, 1)
(49996, 90, 9) (49996, 1)
(63049, 90, 9) (63049, 1)
(64836, 90, 9) (64836, 1)
(64007, 90, 9) (64007, 1)
(69858, 90, 9) (69858, 1)
(56491, 90, 9) (56491, 1)
(65359, 90, 9) (65359, 1)
(61733, 90, 9) (61733, 1)
(66320, 90, 9) (66320, 1)
(61236, 90, 9) (61236, 1)
(71305, 90, 9) (71305, 1)
(52888, 90, 9) (52888, 1)
(58160, 90, 9) (58160, 1)
(70972, 90, 9) (70972, 1)
(61987, 90, 9) (61987, 1)
(43972, 90, 

In [15]:
%%time
S = 3
lstm_lbskd = copy.deepcopy(lstm)
outputs_lbskd1, targets_lbskd1, loss_lbskd1, smape_lbskd1, mae_lbskd1, rmse_lbskd1,global_model, aggregated_logits = fedavg(
    global_model = lstm_lbskd,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = 1,
    model_type = model_type,
    device = device,
)
outputs_lbskd, targets_lbskd, loss_lbskd, smape_lbskd, mae_lbskd, rmse_lbskd = fedlbskd(
    global_model = global_model,
    aggregated_logits=aggregated_logits,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,

    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds-1,
    model_type = model_type,
    device = device,
    S=S
)


starting avg round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49]
round 0, starting client 1/50, id: 0
Epoch [1/1], Train Loss: 0.0889986383746255
round 0, starting client 2/50, id: 1
Epoch [1/1], Train Loss: 0.07721613488263554
round 0, starting client 3/50, id: 2
Epoch [1/1], Train Loss: 0.06492493125713532
round 0, starting client 4/50, id: 3
Epoch [1/1], Train Loss: 0.06847643625794672
round 0, starting client 5/50, id: 4
Epoch [1/1], Train Loss: 0.08233322702686895
round 0, starting client 6/50, id: 5
Epoch [1/1], Train Loss: 0.07239128379151223
round 0, starting client 7/50, id: 6
Epoch [1/1], Train Loss: 0.0892609113172905
round 0, starting client 8/50, id: 7
Epoch [1/1], Train Loss: 0.07425101656677587
round 0, starting client 9/50, id: 8
Epoch [1/1], Train Loss: 0.07519693504302546
round 0, starting client 10/50, id: 9
Epoch [1/1], Train Loss: 0.0652426457274

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.06356934025743097
round 1, starting client 2/50, id: 1
Epoch [1/1], Train Loss: 0.05312258158293036
round 1, starting client 3/50, id: 2
Epoch [1/1], Train Loss: 0.045106070944004595
round 1, starting client 4/50, id: 3
Epoch [1/1], Train Loss: 0.05017214436449256
round 1, starting client 5/50, id: 4
Epoch [1/1], Train Loss: 0.05719350816004657
round 1, starting client 6/50, id: 5
Epoch [1/1], Train Loss: 0.05092589030973615
round 1, starting client 7/50, id: 6
Epoch [1/1], Train Loss: 0.0624393742732905
round 1, starting client 8/50, id: 7
Epoch [1/1], Train Loss: 0.049784106782303654
round 1, starting client 9/50, id: 8
Epoch [1/1], Train Loss: 0.05484091608713453
round 1, starting client 10/50, id: 9
Epoch [1/1], Train Loss: 0.04515565114302767
round 1, starting client 11/50, id: 10
Epoch [1/1], Train Loss: 0.06357889890205115
round 1, starting client 12/50, id: 11
Epoch [1/1], Train Loss: 0.039636401508591684
round 1, starting client 13/50, id: 12
Epoch [

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.05066798613318856
updating loss and weight
round 2, starting client 2/50, id: 1
Epoch [1/1], Train Loss: 0.042440462484955796
updating loss and weight
round 2, starting client 3/50, id: 2
Epoch [1/1], Train Loss: 0.03813799411161907
updating loss and weight
round 2, starting client 4/50, id: 3
Epoch [1/1], Train Loss: 0.04295913115435955
updating loss and weight
round 2, starting client 5/50, id: 4
Epoch [1/1], Train Loss: 0.045461006504906844
updating loss and weight
round 2, starting client 6/50, id: 5
Epoch [1/1], Train Loss: 0.0418566752690822
updating loss and weight
round 2, starting client 7/50, id: 6
Epoch [1/1], Train Loss: 0.048754836558490194
updating loss and weight
round 2, starting client 8/50, id: 7
Epoch [1/1], Train Loss: 0.03902511221339119
updating loss and weight
round 2, starting client 9/50, id: 8
Epoch [1/1], Train Loss: 0.04594928044109389
updating loss and weight
round 2, starting client 10/50, id: 9
Epoch [1/1], Train Loss: 0.0365189

...

Epoch [1/1], Train Loss: 0.0020414782778078785
round 96, starting client 2/50, id: 1
Epoch [1/1], Train Loss: 0.0019268578435811734
round 96, starting client 3/50, id: 2
Epoch [1/1], Train Loss: 0.0024100261337783495
round 96, starting client 4/50, id: 3
Epoch [1/1], Train Loss: 0.0023222953074283023
round 96, starting client 5/50, id: 4
Epoch [1/1], Train Loss: 0.002046174085328609
round 96, starting client 6/50, id: 5
Epoch [1/1], Train Loss: 0.002010755533410702
round 96, starting client 7/50, id: 6
Epoch [1/1], Train Loss: 0.0019019405952201706
round 96, starting client 8/50, id: 7
Epoch [1/1], Train Loss: 0.0034074635675422995
round 96, starting client 9/50, id: 8
Epoch [1/1], Train Loss: 0.002594569362162684
round 96, starting client 10/50, id: 9
Epoch [1/1], Train Loss: 0.0018983133456829276
round 96, starting client 11/50, id: 10
Epoch [1/1], Train Loss: 0.0022173791221575803
round 96, starting client 12/50, id: 11
Epoch [1/1], Train Loss: 0.0020153131519787403
round 96, starti

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0018272936445186446
round 97, starting client 2/50, id: 1
Epoch [1/1], Train Loss: 0.00190561385695926
round 97, starting client 3/50, id: 2
Epoch [1/1], Train Loss: 0.0022585396056658477
round 97, starting client 4/50, id: 3
Epoch [1/1], Train Loss: 0.002317865318664367
round 97, starting client 5/50, id: 4
Epoch [1/1], Train Loss: 0.0020565246959449723
round 97, starting client 6/50, id: 5
Epoch [1/1], Train Loss: 0.0020299153024097905
round 97, starting client 7/50, id: 6
Epoch [1/1], Train Loss: 0.0019051212458745456
round 97, starting client 8/50, id: 7
Epoch [1/1], Train Loss: 0.001455066106743443
round 97, starting client 9/50, id: 8
Epoch [1/1], Train Loss: 0.002585732104937331
round 97, starting client 10/50, id: 9
Epoch [1/1], Train Loss: 0.001909263955625378
round 97, starting client 11/50, id: 10
Epoch [1/1], Train Loss: 0.0021681015423382632
round 97, starting client 12/50, id: 11
Epoch [1/1], Train Loss: 0.002011260477286812
round 97, starting c

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0018249743882751198
updating loss and weight
round 98, starting client 2/50, id: 1
Epoch [1/1], Train Loss: 0.0018998505838681012
updating loss and weight
round 98, starting client 3/50, id: 2
Epoch [1/1], Train Loss: 0.002248043669775749
updating loss and weight
round 98, starting client 4/50, id: 3
Epoch [1/1], Train Loss: 0.002306625128303673
updating loss and weight
round 98, starting client 5/50, id: 4
Epoch [1/1], Train Loss: 0.002050091951704499
updating loss and weight
round 98, starting client 6/50, id: 5
Epoch [1/1], Train Loss: 0.0020206517037877347
updating loss and weight
round 98, starting client 7/50, id: 6
Epoch [1/1], Train Loss: 0.001898817821858904
updating loss and weight
round 98, starting client 8/50, id: 7
Epoch [1/1], Train Loss: 0.0014519458164390666
updating loss and weight
round 98, starting client 9/50, id: 8
Epoch [1/1], Train Loss: 0.0025765979326724145
updating loss and weight
round 98, starting client 10/50, id: 9
Epoch [1/1], 

In [16]:
loss_lbskd = np.insert(loss_lbskd, 0, loss_lbskd1)
smape_lbskd = np.insert(smape_lbskd, 0, smape_lbskd1)
mae_lbskd = np.insert(mae_lbskd, 0, mae_lbskd1)
rmse_lbskd = np.insert(mae_lbskd, 0, mae_lbskd1)

In [17]:
np.save(f'metrics/fedlbskd_outputs_C{n_clients}.npy', np.array(outputs_lbskd, dtype=object))
np.save(f'metrics/fedlbskd_targets_C{n_clients}.npy', np.array(targets_lbskd, dtype=object))
np.save(f'metrics/fedlbskd_loss_C{n_clients}.npy', loss_lbskd)
np.save(f'metrics/fedlbskd_smape_C{n_clients}.npy', smape_lbskd)
np.save(f'metrics/fedlbskd_mae_C{n_clients}.npy', mae_lbskd)
np.save(f'metrics/fedlbskd_rmse_C{n_clients}.npy', rmse_lbskd)

## 60

In [9]:
n_clients=60

In [10]:
train_loader = []
test_loader = []
label_scalers = []
i=0
for _, df in dataframes.items():
    if i==n_clients:
        break
    inputs_cols_indices = range(0, df.shape[1])  # use (total_demand,Year,Month,Day,Hour,Minute) columns as features
    #move the window
    inputs, labels = move_sliding_window(
        df.values,
        window_size,
        inputs_cols_indices=inputs_cols_indices,
        label_col_index=label_col_index
    )

    # Normalize the input data columns
    sc = MinMaxScaler()
    # Obtaining the scaler for the labels(usage data) so that output can be re-scaled to actual value during evaluation
    label_sc = MinMaxScaler()

    # Split data into train/test portions and combining all data into a single array
    test_portion = int(0.2 * len(inputs))

    train_x = sc.fit_transform(inputs[:-test_portion].reshape(-1, window_size * df.shape[1]))
    train_x = train_x.reshape(-1, window_size, df.shape[1])
    train_y = label_sc.fit_transform(labels[:-test_portion])

    test_x = sc.transform(inputs[-test_portion:].reshape(-1, window_size * df.shape[1]))
    test_x = test_x.reshape(-1, window_size, df.shape[1])
    test_y = label_sc.transform(labels[-test_portion:])

    # test_x.append(testx)
    # test_y.append(testy)
    label_scalers.append(label_sc)

    # pytorch data loaders
    train_data = TensorDataset(torch.from_numpy(train_x).to('cpu'), torch.from_numpy(train_y).to('cpu'))
    train_loader.append(DataLoader(train_data, batch_size=batch_size, drop_last=True))# Drop the last incomplete batch
    test_data = TensorDataset(torch.from_numpy(test_x).to('cpu'), torch.from_numpy(test_y).to('cpu'))
    test_loader.append(DataLoader(test_data, batch_size=batch_size))# Drop the last incomplete batch

    # release some memory
    del train_x, train_y
    i=i+1
input_dim = next(iter(train_loader[0]))[0].shape[2]  # 22

(68093, 90, 9) (68093, 1)
(58528, 90, 9) (58528, 1)
(46750, 90, 9) (46750, 1)
(65300, 90, 9) (65300, 1)
(57086, 90, 9) (57086, 1)
(51617, 90, 9) (51617, 1)
(47363, 90, 9) (47363, 1)
(68901, 90, 9) (68901, 1)
(67168, 90, 9) (67168, 1)
(69578, 90, 9) (69578, 1)
(62003, 90, 9) (62003, 1)
(49050, 90, 9) (49050, 1)
(61853, 90, 9) (61853, 1)
(69521, 90, 9) (69521, 1)
(67302, 90, 9) (67302, 1)
(72217, 90, 9) (72217, 1)
(46055, 90, 9) (46055, 1)
(57157, 90, 9) (57157, 1)
(64807, 90, 9) (64807, 1)
(66845, 90, 9) (66845, 1)
(61800, 90, 9) (61800, 1)
(55024, 90, 9) (55024, 1)
(65910, 90, 9) (65910, 1)
(49996, 90, 9) (49996, 1)
(63049, 90, 9) (63049, 1)
(64836, 90, 9) (64836, 1)
(64007, 90, 9) (64007, 1)
(69858, 90, 9) (69858, 1)
(56491, 90, 9) (56491, 1)
(65359, 90, 9) (65359, 1)
(61733, 90, 9) (61733, 1)
(66320, 90, 9) (66320, 1)
(61236, 90, 9) (61236, 1)
(71305, 90, 9) (71305, 1)
(52888, 90, 9) (52888, 1)
(58160, 90, 9) (58160, 1)
(70972, 90, 9) (70972, 1)
(61987, 90, 9) (61987, 1)
(43972, 90, 

In [11]:
%%time
S = 3
lstm_lbskd = copy.deepcopy(lstm)
outputs_lbskd1, targets_lbskd1, loss_lbskd1, smape_lbskd1, mae_lbskd1, rmse_lbskd1,global_model, aggregated_logits = fedavg(
    global_model = lstm_lbskd,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = 1,
    model_type = model_type,
    device = device,
)
outputs_lbskd, targets_lbskd, loss_lbskd, smape_lbskd, mae_lbskd, rmse_lbskd = fedlbskd(
    global_model = global_model,
    aggregated_logits=aggregated_logits,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,

    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds-1,
    model_type = model_type,
    device = device,
    S=S
)


starting avg round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59]
round 0, starting client 1/60, id: 0
Epoch [1/1], Train Loss: 0.07580885041575389
round 0, starting client 2/60, id: 1
Epoch [1/1], Train Loss: 0.06465330419854985
round 0, starting client 3/60, id: 2
Epoch [1/1], Train Loss: 0.054184087474520005
round 0, starting client 4/60, id: 3
Epoch [1/1], Train Loss: 0.05847487204215105
round 0, starting client 5/60, id: 4
Epoch [1/1], Train Loss: 0.06936493050307037
round 0, starting client 6/60, id: 5
Epoch [1/1], Train Loss: 0.06099303336814045
round 0, starting client 7/60, id: 6
Epoch [1/1], Train Loss: 0.07524799656223605
round 0, starting client 8/60, id: 7
Epoch [1/1], Train Loss: 0.061574878979404016
round 0, starting client 9/60, id: 8
Epoch [1/1], Train Loss: 0.06427266531122418
round 0, starting client 10/60, id: 9
Epoch 

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.058058768053943256
round 1, starting client 2/60, id: 1
Epoch [1/1], Train Loss: 0.04831688068807125
round 1, starting client 3/60, id: 2
Epoch [1/1], Train Loss: 0.041592148029141955
round 1, starting client 4/60, id: 3
Epoch [1/1], Train Loss: 0.047040192300782484
round 1, starting client 5/60, id: 4
Epoch [1/1], Train Loss: 0.05197319062426686
round 1, starting client 6/60, id: 5
Epoch [1/1], Train Loss: 0.04690614980645479
round 1, starting client 7/60, id: 6
Epoch [1/1], Train Loss: 0.056275600114384226
round 1, starting client 8/60, id: 7
Epoch [1/1], Train Loss: 0.044955044949673256
round 1, starting client 9/60, id: 8
Epoch [1/1], Train Loss: 0.05082463501737668
round 1, starting client 10/60, id: 9
Epoch [1/1], Train Loss: 0.041499492815799184
round 1, starting client 11/60, id: 10
Epoch [1/1], Train Loss: 0.05802329509363821
round 1, starting client 12/60, id: 11
Epoch [1/1], Train Loss: 0.0362022685769357
round 1, starting client 13/60, id: 12
Epoc

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.04834206275782493
updating loss and weight
round 2, starting client 2/60, id: 1
Epoch [1/1], Train Loss: 0.04085098707841504
updating loss and weight
round 2, starting client 3/60, id: 2
Epoch [1/1], Train Loss: 0.03723426903080609
updating loss and weight
round 2, starting client 4/60, id: 3
Epoch [1/1], Train Loss: 0.041761843925889795
updating loss and weight
round 2, starting client 5/60, id: 4
Epoch [1/1], Train Loss: 0.043498822403225036
updating loss and weight
round 2, starting client 6/60, id: 5
Epoch [1/1], Train Loss: 0.04074362930841745
updating loss and weight
round 2, starting client 7/60, id: 6
Epoch [1/1], Train Loss: 0.046870956600115095
updating loss and weight
round 2, starting client 8/60, id: 7
Epoch [1/1], Train Loss: 0.03715167809629215
updating loss and weight
round 2, starting client 9/60, id: 8
Epoch [1/1], Train Loss: 0.043970905280170544
updating loss and weight
round 2, starting client 10/60, id: 9
Epoch [1/1], Train Loss: 0.03499

...

Epoch [1/1], Train Loss: 0.0018363734729201443
round 96, starting client 2/60, id: 1
Epoch [1/1], Train Loss: 0.0019152495324508188
round 96, starting client 3/60, id: 2
Epoch [1/1], Train Loss: 0.002066835636570532
round 96, starting client 4/60, id: 3
Epoch [1/1], Train Loss: 0.0023217499530052443
round 96, starting client 5/60, id: 4
Epoch [1/1], Train Loss: 0.0020438073869709942
round 96, starting client 6/60, id: 5
Epoch [1/1], Train Loss: 0.0019890807794581632
round 96, starting client 7/60, id: 6
Epoch [1/1], Train Loss: 0.001973307779612573
round 96, starting client 8/60, id: 7
Epoch [1/1], Train Loss: 0.001607940943015493
round 96, starting client 9/60, id: 8
Epoch [1/1], Train Loss: 0.002949155992470109
round 96, starting client 10/60, id: 9
Epoch [1/1], Train Loss: 0.0018983733170898631
round 96, starting client 11/60, id: 10
Epoch [1/1], Train Loss: 0.002184579431438275
round 96, starting client 12/60, id: 11
Epoch [1/1], Train Loss: 0.0019915227435137093
round 96, starting

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.001847525586852944
round 97, starting client 2/60, id: 1
Epoch [1/1], Train Loss: 0.0018953157433619105
round 97, starting client 3/60, id: 2
Epoch [1/1], Train Loss: 0.002163518781243409
round 97, starting client 4/60, id: 3
Epoch [1/1], Train Loss: 0.0022979695093133215
round 97, starting client 5/60, id: 4
Epoch [1/1], Train Loss: 0.0020368742526360706
round 97, starting client 6/60, id: 5
Epoch [1/1], Train Loss: 0.00198663887422299
round 97, starting client 7/60, id: 6
Epoch [1/1], Train Loss: 0.001895829314693204
round 97, starting client 8/60, id: 7
Epoch [1/1], Train Loss: 0.0014514888264458487
round 97, starting client 9/60, id: 8
Epoch [1/1], Train Loss: 0.002555614796270115
round 97, starting client 10/60, id: 9
Epoch [1/1], Train Loss: 0.001879006217307135
round 97, starting client 11/60, id: 10
Epoch [1/1], Train Loss: 0.002159094058394354
round 97, starting client 12/60, id: 11
Epoch [1/1], Train Loss: 0.0019878397410809014
round 97, starting cl

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0018416501742014482
updating loss and weight
round 98, starting client 2/60, id: 1
Epoch [1/1], Train Loss: 0.0018896304349052828
updating loss and weight
round 98, starting client 3/60, id: 2
Epoch [1/1], Train Loss: 0.002152495219585641
updating loss and weight
round 98, starting client 4/60, id: 3
Epoch [1/1], Train Loss: 0.0022912896529305726
updating loss and weight
round 98, starting client 5/60, id: 4
Epoch [1/1], Train Loss: 0.002032078613410704
updating loss and weight
round 98, starting client 6/60, id: 5
Epoch [1/1], Train Loss: 0.001980825153441402
updating loss and weight
round 98, starting client 7/60, id: 6
Epoch [1/1], Train Loss: 0.0018873703492981557
updating loss and weight
round 98, starting client 8/60, id: 7
Epoch [1/1], Train Loss: 0.001447215097525842
updating loss and weight
round 98, starting client 9/60, id: 8
Epoch [1/1], Train Loss: 0.002547064719972416
updating loss and weight
round 98, starting client 10/60, id: 9
Epoch [1/1], T

In [12]:
loss_lbskd = np.insert(loss_lbskd, 0, loss_lbskd1)
smape_lbskd = np.insert(smape_lbskd, 0, smape_lbskd1)
mae_lbskd = np.insert(mae_lbskd, 0, mae_lbskd1)
rmse_lbskd = np.insert(mae_lbskd, 0, mae_lbskd1)

In [13]:
np.save(f'metrics/fedlbskd_outputs_C{n_clients}.npy', np.array(outputs_lbskd, dtype=object))
np.save(f'metrics/fedlbskd_targets_C{n_clients}.npy', np.array(targets_lbskd, dtype=object))
np.save(f'metrics/fedlbskd_loss_C{n_clients}.npy', loss_lbskd)
np.save(f'metrics/fedlbskd_smape_C{n_clients}.npy', smape_lbskd)
np.save(f'metrics/fedlbskd_mae_C{n_clients}.npy', mae_lbskd)
np.save(f'metrics/fedlbskd_rmse_C{n_clients}.npy', rmse_lbskd)

## 70

In [14]:
n_clients=70

In [15]:
train_loader = []
test_loader = []
label_scalers = []
i=0
for _, df in dataframes.items():
    if i==n_clients:
        break
    inputs_cols_indices = range(0, df.shape[1])  # use (total_demand,Year,Month,Day,Hour,Minute) columns as features
    #move the window
    inputs, labels = move_sliding_window(
        df.values,
        window_size,
        inputs_cols_indices=inputs_cols_indices,
        label_col_index=label_col_index
    )

    # Normalize the input data columns
    sc = MinMaxScaler()
    # Obtaining the scaler for the labels(usage data) so that output can be re-scaled to actual value during evaluation
    label_sc = MinMaxScaler()

    # Split data into train/test portions and combining all data into a single array
    test_portion = int(0.2 * len(inputs))

    train_x = sc.fit_transform(inputs[:-test_portion].reshape(-1, window_size * df.shape[1]))
    train_x = train_x.reshape(-1, window_size, df.shape[1])
    train_y = label_sc.fit_transform(labels[:-test_portion])

    test_x = sc.transform(inputs[-test_portion:].reshape(-1, window_size * df.shape[1]))
    test_x = test_x.reshape(-1, window_size, df.shape[1])
    test_y = label_sc.transform(labels[-test_portion:])

    # test_x.append(testx)
    # test_y.append(testy)
    label_scalers.append(label_sc)

    # pytorch data loaders
    train_data = TensorDataset(torch.from_numpy(train_x).to('cpu'), torch.from_numpy(train_y).to('cpu'))
    train_loader.append(DataLoader(train_data, batch_size=batch_size, drop_last=True))# Drop the last incomplete batch
    test_data = TensorDataset(torch.from_numpy(test_x).to('cpu'), torch.from_numpy(test_y).to('cpu'))
    test_loader.append(DataLoader(test_data, batch_size=batch_size))# Drop the last incomplete batch

    # release some memory
    del train_x, train_y
    i=i+1
input_dim = next(iter(train_loader[0]))[0].shape[2]  # 22

(68093, 90, 9) (68093, 1)
(58528, 90, 9) (58528, 1)
(46750, 90, 9) (46750, 1)
(65300, 90, 9) (65300, 1)
(57086, 90, 9) (57086, 1)
(51617, 90, 9) (51617, 1)
(47363, 90, 9) (47363, 1)
(68901, 90, 9) (68901, 1)
(67168, 90, 9) (67168, 1)
(69578, 90, 9) (69578, 1)
(62003, 90, 9) (62003, 1)
(49050, 90, 9) (49050, 1)
(61853, 90, 9) (61853, 1)
(69521, 90, 9) (69521, 1)
(67302, 90, 9) (67302, 1)
(72217, 90, 9) (72217, 1)
(46055, 90, 9) (46055, 1)
(57157, 90, 9) (57157, 1)
(64807, 90, 9) (64807, 1)
(66845, 90, 9) (66845, 1)
(61800, 90, 9) (61800, 1)
(55024, 90, 9) (55024, 1)
(65910, 90, 9) (65910, 1)
(49996, 90, 9) (49996, 1)
(63049, 90, 9) (63049, 1)
(64836, 90, 9) (64836, 1)
(64007, 90, 9) (64007, 1)
(69858, 90, 9) (69858, 1)
(56491, 90, 9) (56491, 1)
(65359, 90, 9) (65359, 1)
(61733, 90, 9) (61733, 1)
(66320, 90, 9) (66320, 1)
(61236, 90, 9) (61236, 1)
(71305, 90, 9) (71305, 1)
(52888, 90, 9) (52888, 1)
(58160, 90, 9) (58160, 1)
(70972, 90, 9) (70972, 1)
(61987, 90, 9) (61987, 1)
(43972, 90, 

In [16]:
%%time
S = 3
lstm_lbskd = copy.deepcopy(lstm)
outputs_lbskd1, targets_lbskd1, loss_lbskd1, smape_lbskd1, mae_lbskd1, rmse_lbskd1,global_model, aggregated_logits = fedavg(
    global_model = lstm_lbskd,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = 1,
    model_type = model_type,
    device = device,
)
outputs_lbskd, targets_lbskd, loss_lbskd, smape_lbskd, mae_lbskd, rmse_lbskd = fedlbskd(
    global_model = global_model,
    aggregated_logits=aggregated_logits,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,

    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds-1,
    model_type = model_type,
    device = device,
    S=S
)


starting avg round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69]
round 0, starting client 1/70, id: 0
Epoch [1/1], Train Loss: 0.07580885041575389
round 0, starting client 2/70, id: 1
Epoch [1/1], Train Loss: 0.06465330419854985
round 0, starting client 3/70, id: 2
Epoch [1/1], Train Loss: 0.054184087474520005
round 0, starting client 4/70, id: 3
Epoch [1/1], Train Loss: 0.05847487204215105
round 0, starting client 5/70, id: 4
Epoch [1/1], Train Loss: 0.06936493050307037
round 0, starting client 6/70, id: 5
Epoch [1/1], Train Loss: 0.06099303336814045
round 0, starting client 7/70, id: 6
Epoch [1/1], Train Loss: 0.07524799656223605
round 0, starting client 8/70, id: 7
Epoch [1/1], Train Loss: 0.061574878979404016
round 0, starting client 9/70, id: 8
Epoch [1/1], Train Loss: 0.06427266531122418
round 0, start

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.05806270424487456
round 1, starting client 2/70, id: 1
Epoch [1/1], Train Loss: 0.04831909694605405
round 1, starting client 3/70, id: 2
Epoch [1/1], Train Loss: 0.041591227390906885
round 1, starting client 4/70, id: 3
Epoch [1/1], Train Loss: 0.04703808592303711
round 1, starting client 5/70, id: 4
Epoch [1/1], Train Loss: 0.05197589192539453
round 1, starting client 6/70, id: 5
Epoch [1/1], Train Loss: 0.046905594971030945
round 1, starting client 7/70, id: 6
Epoch [1/1], Train Loss: 0.056280950738771554
round 1, starting client 8/70, id: 7
Epoch [1/1], Train Loss: 0.04495892139538277
round 1, starting client 9/70, id: 8
Epoch [1/1], Train Loss: 0.050823922627247296
round 1, starting client 10/70, id: 9
Epoch [1/1], Train Loss: 0.041498370399629614
round 1, starting client 11/70, id: 10
Epoch [1/1], Train Loss: 0.058026501210406416
round 1, starting client 12/70, id: 11
Epoch [1/1], Train Loss: 0.03620114599011446
round 1, starting client 13/70, id: 12
Epo

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.04833086326999484
updating loss and weight
round 2, starting client 2/70, id: 1
Epoch [1/1], Train Loss: 0.04082324848406845
updating loss and weight
round 2, starting client 3/70, id: 2
Epoch [1/1], Train Loss: 0.03719043369508452
updating loss and weight
round 2, starting client 4/70, id: 3
Epoch [1/1], Train Loss: 0.041720385973652206
updating loss and weight
round 2, starting client 5/70, id: 4
Epoch [1/1], Train Loss: 0.04347639293833214
updating loss and weight
round 2, starting client 6/70, id: 5
Epoch [1/1], Train Loss: 0.04070962830446661
updating loss and weight
round 2, starting client 7/70, id: 6
Epoch [1/1], Train Loss: 0.04685048869735487
updating loss and weight
round 2, starting client 8/70, id: 7
Epoch [1/1], Train Loss: 0.03713438666935237
updating loss and weight
round 2, starting client 9/70, id: 8
Epoch [1/1], Train Loss: 0.04394460215161628
updating loss and weight
round 2, starting client 10/70, id: 9
Epoch [1/1], Train Loss: 0.03496402

...

Epoch [1/1], Train Loss: 0.0019915955732049385
round 96, starting client 2/70, id: 1
Epoch [1/1], Train Loss: 0.001930099342199457
round 96, starting client 3/70, id: 2
Epoch [1/1], Train Loss: 0.0022313866809579646
round 96, starting client 4/70, id: 3
Epoch [1/1], Train Loss: 0.002296599491006311
round 96, starting client 5/70, id: 4
Epoch [1/1], Train Loss: 0.0020362053024159236
round 96, starting client 6/70, id: 5
Epoch [1/1], Train Loss: 0.0019788038902333934
round 96, starting client 7/70, id: 6
Epoch [1/1], Train Loss: 0.0019490216776879659
round 96, starting client 8/70, id: 7
Epoch [1/1], Train Loss: 0.0030117172370049752
round 96, starting client 9/70, id: 8
Epoch [1/1], Train Loss: 0.0026566289340665275
round 96, starting client 10/70, id: 9
Epoch [1/1], Train Loss: 0.0018879057350676257
round 96, starting client 11/70, id: 10
Epoch [1/1], Train Loss: 0.0022071883286116636
round 96, starting client 12/70, id: 11
Epoch [1/1], Train Loss: 0.00196801041448979
round 96, startin

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.001837455987148338
round 97, starting client 2/70, id: 1
Epoch [1/1], Train Loss: 0.0018897575455614267
round 97, starting client 3/70, id: 2
Epoch [1/1], Train Loss: 0.0021250816458228254
round 97, starting client 4/70, id: 3
Epoch [1/1], Train Loss: 0.002281112193504312
round 97, starting client 5/70, id: 4
Epoch [1/1], Train Loss: 0.002027434274416671
round 97, starting client 6/70, id: 5
Epoch [1/1], Train Loss: 0.0019752807129407306
round 97, starting client 7/70, id: 6
Epoch [1/1], Train Loss: 0.0018911221350945938
round 97, starting client 8/70, id: 7
Epoch [1/1], Train Loss: 0.0014421159180786178
round 97, starting client 9/70, id: 8
Epoch [1/1], Train Loss: 0.002537012999080337
round 97, starting client 10/70, id: 9
Epoch [1/1], Train Loss: 0.0018671521476655328
round 97, starting client 11/70, id: 10
Epoch [1/1], Train Loss: 0.0021473473243531775
round 97, starting client 12/70, id: 11
Epoch [1/1], Train Loss: 0.001973321183437579
round 97, starting

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0018322502025666662
updating loss and weight
round 98, starting client 2/70, id: 1
Epoch [1/1], Train Loss: 0.0018836707859817478
updating loss and weight
round 98, starting client 3/70, id: 2
Epoch [1/1], Train Loss: 0.0021105207205336135
updating loss and weight
round 98, starting client 4/70, id: 3
Epoch [1/1], Train Loss: 0.002274202350664007
updating loss and weight
round 98, starting client 5/70, id: 4
Epoch [1/1], Train Loss: 0.002023167902900076
updating loss and weight
round 98, starting client 6/70, id: 5
Epoch [1/1], Train Loss: 0.001968897441838635
updating loss and weight
round 98, starting client 7/70, id: 6
Epoch [1/1], Train Loss: 0.0018971841876722273
updating loss and weight
round 98, starting client 8/70, id: 7
Epoch [1/1], Train Loss: 0.0014389901342889613
updating loss and weight
round 98, starting client 9/70, id: 8
Epoch [1/1], Train Loss: 0.0025280936623368264
updating loss and weight
round 98, starting client 10/70, id: 9
Epoch [1/1],

In [17]:
loss_lbskd = np.insert(loss_lbskd, 0, loss_lbskd1)
smape_lbskd = np.insert(smape_lbskd, 0, smape_lbskd1)
mae_lbskd = np.insert(mae_lbskd, 0, mae_lbskd1)
rmse_lbskd = np.insert(mae_lbskd, 0, mae_lbskd1)

In [18]:
np.save(f'metrics/fedlbskd_outputs_C{n_clients}.npy', np.array(outputs_lbskd, dtype=object))
np.save(f'metrics/fedlbskd_targets_C{n_clients}.npy', np.array(targets_lbskd, dtype=object))
np.save(f'metrics/fedlbskd_loss_C{n_clients}.npy', loss_lbskd)
np.save(f'metrics/fedlbskd_smape_C{n_clients}.npy', smape_lbskd)
np.save(f'metrics/fedlbskd_mae_C{n_clients}.npy', mae_lbskd)
np.save(f'metrics/fedlbskd_rmse_C{n_clients}.npy', rmse_lbskd)

## 80

In [19]:
n_clients=80

In [20]:
train_loader = []
test_loader = []
label_scalers = []
i=0
for _, df in dataframes.items():
    if i==n_clients:
        break
    inputs_cols_indices = range(0, df.shape[1])  # use (total_demand,Year,Month,Day,Hour,Minute) columns as features
    #move the window
    inputs, labels = move_sliding_window(
        df.values,
        window_size,
        inputs_cols_indices=inputs_cols_indices,
        label_col_index=label_col_index
    )

    # Normalize the input data columns
    sc = MinMaxScaler()
    # Obtaining the scaler for the labels(usage data) so that output can be re-scaled to actual value during evaluation
    label_sc = MinMaxScaler()

    # Split data into train/test portions and combining all data into a single array
    test_portion = int(0.2 * len(inputs))

    train_x = sc.fit_transform(inputs[:-test_portion].reshape(-1, window_size * df.shape[1]))
    train_x = train_x.reshape(-1, window_size, df.shape[1])
    train_y = label_sc.fit_transform(labels[:-test_portion])

    test_x = sc.transform(inputs[-test_portion:].reshape(-1, window_size * df.shape[1]))
    test_x = test_x.reshape(-1, window_size, df.shape[1])
    test_y = label_sc.transform(labels[-test_portion:])

    # test_x.append(testx)
    # test_y.append(testy)
    label_scalers.append(label_sc)

    # pytorch data loaders
    train_data = TensorDataset(torch.from_numpy(train_x).to('cpu'), torch.from_numpy(train_y).to('cpu'))
    train_loader.append(DataLoader(train_data, batch_size=batch_size, drop_last=True))# Drop the last incomplete batch
    test_data = TensorDataset(torch.from_numpy(test_x).to('cpu'), torch.from_numpy(test_y).to('cpu'))
    test_loader.append(DataLoader(test_data, batch_size=batch_size))# Drop the last incomplete batch

    # release some memory
    del train_x, train_y
    i=i+1
input_dim = next(iter(train_loader[0]))[0].shape[2]  # 22

(68093, 90, 9) (68093, 1)
(58528, 90, 9) (58528, 1)
(46750, 90, 9) (46750, 1)
(65300, 90, 9) (65300, 1)
(57086, 90, 9) (57086, 1)
(51617, 90, 9) (51617, 1)
(47363, 90, 9) (47363, 1)
(68901, 90, 9) (68901, 1)
(67168, 90, 9) (67168, 1)
(69578, 90, 9) (69578, 1)
(62003, 90, 9) (62003, 1)
(49050, 90, 9) (49050, 1)
(61853, 90, 9) (61853, 1)
(69521, 90, 9) (69521, 1)
(67302, 90, 9) (67302, 1)
(72217, 90, 9) (72217, 1)
(46055, 90, 9) (46055, 1)
(57157, 90, 9) (57157, 1)
(64807, 90, 9) (64807, 1)
(66845, 90, 9) (66845, 1)
(61800, 90, 9) (61800, 1)
(55024, 90, 9) (55024, 1)
(65910, 90, 9) (65910, 1)
(49996, 90, 9) (49996, 1)
(63049, 90, 9) (63049, 1)
(64836, 90, 9) (64836, 1)
(64007, 90, 9) (64007, 1)
(69858, 90, 9) (69858, 1)
(56491, 90, 9) (56491, 1)
(65359, 90, 9) (65359, 1)
(61733, 90, 9) (61733, 1)
(66320, 90, 9) (66320, 1)
(61236, 90, 9) (61236, 1)
(71305, 90, 9) (71305, 1)
(52888, 90, 9) (52888, 1)
(58160, 90, 9) (58160, 1)
(70972, 90, 9) (70972, 1)
(61987, 90, 9) (61987, 1)
(43972, 90, 

In [21]:
%%time
S = 3
lstm_lbskd = copy.deepcopy(lstm)
outputs_lbskd1, targets_lbskd1, loss_lbskd1, smape_lbskd1, mae_lbskd1, rmse_lbskd1,global_model, aggregated_logits = fedavg(
    global_model = lstm_lbskd,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = 1,
    model_type = model_type,
    device = device,
)
outputs_lbskd, targets_lbskd, loss_lbskd, smape_lbskd, mae_lbskd, rmse_lbskd = fedlbskd(
    global_model = global_model,
    aggregated_logits=aggregated_logits,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,

    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds-1,
    model_type = model_type,
    device = device,
    S=S
)


starting avg round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69 70 71
 72 73 74 75 76 77 78 79]
round 0, starting client 1/80, id: 0
Epoch [1/1], Train Loss: 0.07580885041575389
round 0, starting client 2/80, id: 1
Epoch [1/1], Train Loss: 0.06465330419854985
round 0, starting client 3/80, id: 2
Epoch [1/1], Train Loss: 0.054184087474520005
round 0, starting client 4/80, id: 3
Epoch [1/1], Train Loss: 0.05847487204215105
round 0, starting client 5/80, id: 4
Epoch [1/1], Train Loss: 0.06936493050307037
round 0, starting client 6/80, id: 5
Epoch [1/1], Train Loss: 0.06099303336814045
round 0, starting client 7/80, id: 6
Epoch [1/1], Train Loss: 0.07524799656223605
round 0, starting client 8/80, id: 7
Epoch [1/1], Train Loss: 0.061574878979404016
round 0, starting client 9/80, id: 8
Epoch [1/1], Train Loss: 0.0

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.058125144503307795
round 1, starting client 2/80, id: 1
Epoch [1/1], Train Loss: 0.048371349771817534
round 1, starting client 3/80, id: 2
Epoch [1/1], Train Loss: 0.04163038549530837
round 1, starting client 4/80, id: 3
Epoch [1/1], Train Loss: 0.047078627672996
round 1, starting client 5/80, id: 4
Epoch [1/1], Train Loss: 0.05203398668461226
round 1, starting client 6/80, id: 5
Epoch [1/1], Train Loss: 0.046951893903315084
round 1, starting client 7/80, id: 6
Epoch [1/1], Train Loss: 0.05634569844885453
round 1, starting client 8/80, id: 7
Epoch [1/1], Train Loss: 0.045009243952215845
round 1, starting client 9/80, id: 8
Epoch [1/1], Train Loss: 0.050871541222127586
round 1, starting client 10/80, id: 9
Epoch [1/1], Train Loss: 0.041539986514382905
round 1, starting client 11/80, id: 10
Epoch [1/1], Train Loss: 0.058089438127353794
round 1, starting client 12/80, id: 11
Epoch [1/1], Train Loss: 0.0362347327662926
round 1, starting client 13/80, id: 12
Epoch

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.048457612511965474
updating loss and weight
round 2, starting client 2/80, id: 1
Epoch [1/1], Train Loss: 0.04094749478002389
updating loss and weight
round 2, starting client 3/80, id: 2
Epoch [1/1], Train Loss: 0.0373103092941973
updating loss and weight
round 2, starting client 4/80, id: 3
Epoch [1/1], Train Loss: 0.04185829589179918
updating loss and weight
round 2, starting client 5/80, id: 4
Epoch [1/1], Train Loss: 0.04360313747416843
updating loss and weight
round 2, starting client 6/80, id: 5
Epoch [1/1], Train Loss: 0.04083509775809944
updating loss and weight
round 2, starting client 7/80, id: 6
Epoch [1/1], Train Loss: 0.04697932846642829
updating loss and weight
round 2, starting client 8/80, id: 7
Epoch [1/1], Train Loss: 0.037242001520012905
updating loss and weight
round 2, starting client 9/80, id: 8
Epoch [1/1], Train Loss: 0.044074219329139366
updating loss and weight
round 2, starting client 10/80, id: 9
Epoch [1/1], Train Loss: 0.0350819

...

Epoch [1/1], Train Loss: 0.0018476258457049658
round 96, starting client 2/80, id: 1
Epoch [1/1], Train Loss: 0.0019394865350073414
round 96, starting client 3/80, id: 2
Epoch [1/1], Train Loss: 0.00211415529500098
round 96, starting client 4/80, id: 3
Epoch [1/1], Train Loss: 0.0023771523242341534
round 96, starting client 5/80, id: 4
Epoch [1/1], Train Loss: 0.002115816125296987
round 96, starting client 6/80, id: 5
Epoch [1/1], Train Loss: 0.0020435837694094514
round 96, starting client 7/80, id: 6
Epoch [1/1], Train Loss: 0.0019429161329753697
round 96, starting client 8/80, id: 7
Epoch [1/1], Train Loss: 0.0026175589256761766
round 96, starting client 9/80, id: 8
Epoch [1/1], Train Loss: 0.0026848487144049537
round 96, starting client 10/80, id: 9
Epoch [1/1], Train Loss: 0.0019011724507436158
round 96, starting client 11/80, id: 10
Epoch [1/1], Train Loss: 0.002205861463153269
round 96, starting client 12/80, id: 11
Epoch [1/1], Train Loss: 0.002012759327618895
round 96, starting

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.001854470917814464
round 97, starting client 2/80, id: 1
Epoch [1/1], Train Loss: 0.0019227664464981193
round 97, starting client 3/80, id: 2
Epoch [1/1], Train Loss: 0.0021725940023316075
round 97, starting client 4/80, id: 3
Epoch [1/1], Train Loss: 0.0023238379896307984
round 97, starting client 5/80, id: 4
Epoch [1/1], Train Loss: 0.002063098583179949
round 97, starting client 6/80, id: 5
Epoch [1/1], Train Loss: 0.0020185931505693586
round 97, starting client 7/80, id: 6
Epoch [1/1], Train Loss: 0.001917689134102516
round 97, starting client 8/80, id: 7
Epoch [1/1], Train Loss: 0.0014555134035137323
round 97, starting client 9/80, id: 8
Epoch [1/1], Train Loss: 0.0025968144540316784
round 97, starting client 10/80, id: 9
Epoch [1/1], Train Loss: 0.0019035803879550832
round 97, starting client 11/80, id: 10
Epoch [1/1], Train Loss: 0.0021844776492798697
round 97, starting client 12/80, id: 11
Epoch [1/1], Train Loss: 0.0020099242407779546
round 97, starti

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0018481108055775105
updating loss and weight
round 98, starting client 2/80, id: 1
Epoch [1/1], Train Loss: 0.0019157447645233737
updating loss and weight
round 98, starting client 3/80, id: 2
Epoch [1/1], Train Loss: 0.002165858109947293
updating loss and weight
round 98, starting client 4/80, id: 3
Epoch [1/1], Train Loss: 0.0023173714745972386
updating loss and weight
round 98, starting client 5/80, id: 4
Epoch [1/1], Train Loss: 0.002056221562353048
updating loss and weight
round 98, starting client 6/80, id: 5
Epoch [1/1], Train Loss: 0.0020112409634748477
updating loss and weight
round 98, starting client 7/80, id: 6
Epoch [1/1], Train Loss: 0.0019098977507973041
updating loss and weight
round 98, starting client 8/80, id: 7
Epoch [1/1], Train Loss: 0.0014521768514312947
updating loss and weight
round 98, starting client 9/80, id: 8
Epoch [1/1], Train Loss: 0.0025869560777209703
updating loss and weight
round 98, starting client 10/80, id: 9
Epoch [1/1]

In [22]:
loss_lbskd = np.insert(loss_lbskd, 0, loss_lbskd1)
smape_lbskd = np.insert(smape_lbskd, 0, smape_lbskd1)
mae_lbskd = np.insert(mae_lbskd, 0, mae_lbskd1)
rmse_lbskd = np.insert(mae_lbskd, 0, mae_lbskd1)

In [23]:
np.save(f'metrics/fedlbskd_outputs_C{n_clients}.npy', np.array(outputs_lbskd, dtype=object))
np.save(f'metrics/fedlbskd_targets_C{n_clients}.npy', np.array(targets_lbskd, dtype=object))
np.save(f'metrics/fedlbskd_loss_C{n_clients}.npy', loss_lbskd)
np.save(f'metrics/fedlbskd_smape_C{n_clients}.npy', smape_lbskd)
np.save(f'metrics/fedlbskd_mae_C{n_clients}.npy', mae_lbskd)
np.save(f'metrics/fedlbskd_rmse_C{n_clients}.npy', rmse_lbskd)

## 90

In [24]:
n_clients=90

In [25]:
train_loader = []
test_loader = []
label_scalers = []
i=0
for _, df in dataframes.items():
    if i==n_clients:
        break
    inputs_cols_indices = range(0, df.shape[1])  # use (total_demand,Year,Month,Day,Hour,Minute) columns as features
    #move the window
    inputs, labels = move_sliding_window(
        df.values,
        window_size,
        inputs_cols_indices=inputs_cols_indices,
        label_col_index=label_col_index
    )

    # Normalize the input data columns
    sc = MinMaxScaler()
    # Obtaining the scaler for the labels(usage data) so that output can be re-scaled to actual value during evaluation
    label_sc = MinMaxScaler()

    # Split data into train/test portions and combining all data into a single array
    test_portion = int(0.2 * len(inputs))

    train_x = sc.fit_transform(inputs[:-test_portion].reshape(-1, window_size * df.shape[1]))
    train_x = train_x.reshape(-1, window_size, df.shape[1])
    train_y = label_sc.fit_transform(labels[:-test_portion])

    test_x = sc.transform(inputs[-test_portion:].reshape(-1, window_size * df.shape[1]))
    test_x = test_x.reshape(-1, window_size, df.shape[1])
    test_y = label_sc.transform(labels[-test_portion:])

    # test_x.append(testx)
    # test_y.append(testy)
    label_scalers.append(label_sc)

    # pytorch data loaders
    train_data = TensorDataset(torch.from_numpy(train_x).to('cpu'), torch.from_numpy(train_y).to('cpu'))
    train_loader.append(DataLoader(train_data, batch_size=batch_size, drop_last=True))# Drop the last incomplete batch
    test_data = TensorDataset(torch.from_numpy(test_x).to('cpu'), torch.from_numpy(test_y).to('cpu'))
    test_loader.append(DataLoader(test_data, batch_size=batch_size))# Drop the last incomplete batch

    # release some memory
    del train_x, train_y
    i=i+1
input_dim = next(iter(train_loader[0]))[0].shape[2]  # 22

(68093, 90, 9) (68093, 1)
(58528, 90, 9) (58528, 1)
(46750, 90, 9) (46750, 1)
(65300, 90, 9) (65300, 1)
(57086, 90, 9) (57086, 1)
(51617, 90, 9) (51617, 1)
(47363, 90, 9) (47363, 1)
(68901, 90, 9) (68901, 1)
(67168, 90, 9) (67168, 1)
(69578, 90, 9) (69578, 1)
(62003, 90, 9) (62003, 1)
(49050, 90, 9) (49050, 1)
(61853, 90, 9) (61853, 1)
(69521, 90, 9) (69521, 1)
(67302, 90, 9) (67302, 1)
(72217, 90, 9) (72217, 1)
(46055, 90, 9) (46055, 1)
(57157, 90, 9) (57157, 1)
(64807, 90, 9) (64807, 1)
(66845, 90, 9) (66845, 1)
(61800, 90, 9) (61800, 1)
(55024, 90, 9) (55024, 1)
(65910, 90, 9) (65910, 1)
(49996, 90, 9) (49996, 1)
(63049, 90, 9) (63049, 1)
(64836, 90, 9) (64836, 1)
(64007, 90, 9) (64007, 1)
(69858, 90, 9) (69858, 1)
(56491, 90, 9) (56491, 1)
(65359, 90, 9) (65359, 1)
(61733, 90, 9) (61733, 1)
(66320, 90, 9) (66320, 1)
(61236, 90, 9) (61236, 1)
(71305, 90, 9) (71305, 1)
(52888, 90, 9) (52888, 1)
(58160, 90, 9) (58160, 1)
(70972, 90, 9) (70972, 1)
(61987, 90, 9) (61987, 1)
(43972, 90, 

In [26]:
%%time
S = 3
lstm_lbskd = copy.deepcopy(lstm)
outputs_lbskd1, targets_lbskd1, loss_lbskd1, smape_lbskd1, mae_lbskd1, rmse_lbskd1,global_model, aggregated_logits = fedavg(
    global_model = lstm_lbskd,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = 1,
    model_type = model_type,
    device = device,
)
outputs_lbskd, targets_lbskd, loss_lbskd, smape_lbskd, mae_lbskd, rmse_lbskd = fedlbskd(
    global_model = global_model,
    aggregated_logits=aggregated_logits,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,

    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds-1,
    model_type = model_type,
    device = device,
    S=S
)


starting avg round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69 70 71
 72 73 74 75 76 77 78 79 80 81 82 83 84 85 86 87 88 89]
round 0, starting client 1/90, id: 0
Epoch [1/1], Train Loss: 0.07580885041575389
round 0, starting client 2/90, id: 1
Epoch [1/1], Train Loss: 0.06465330419854985
round 0, starting client 3/90, id: 2
Epoch [1/1], Train Loss: 0.054184087474520005
round 0, starting client 4/90, id: 3
Epoch [1/1], Train Loss: 0.05847487204215105
round 0, starting client 5/90, id: 4
Epoch [1/1], Train Loss: 0.06936493050307037
round 0, starting client 6/90, id: 5
Epoch [1/1], Train Loss: 0.06099303336814045
round 0, starting client 7/90, id: 6
Epoch [1/1], Train Loss: 0.07524799656223605
round 0, starting client 8/90, id: 7
Epoch [1/1], Train Loss: 0.061574878979404016
round 0, starting client 9/90, id: 

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.05804371545618435
round 1, starting client 2/90, id: 1
Epoch [1/1], Train Loss: 0.04830130847791831
round 1, starting client 3/90, id: 2
Epoch [1/1], Train Loss: 0.041584883402619094
round 1, starting client 4/90, id: 3
Epoch [1/1], Train Loss: 0.04703611953585756
round 1, starting client 5/90, id: 4
Epoch [1/1], Train Loss: 0.051956660833887086
round 1, starting client 6/90, id: 5
Epoch [1/1], Train Loss: 0.04689583727158607
round 1, starting client 7/90, id: 6
Epoch [1/1], Train Loss: 0.05625783712477298
round 1, starting client 8/90, id: 7
Epoch [1/1], Train Loss: 0.04493636360286542
round 1, starting client 9/90, id: 8
Epoch [1/1], Train Loss: 0.05081823611488708
round 1, starting client 10/90, id: 9
Epoch [1/1], Train Loss: 0.04148795165949397
round 1, starting client 11/90, id: 10
Epoch [1/1], Train Loss: 0.058008765762982265
round 1, starting client 12/90, id: 11
Epoch [1/1], Train Loss: 0.03619424528197239
round 1, starting client 13/90, id: 12
Epoch 

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.04835617876137203
updating loss and weight
round 2, starting client 2/90, id: 1
Epoch [1/1], Train Loss: 0.04089554022583696
updating loss and weight
round 2, starting client 3/90, id: 2
Epoch [1/1], Train Loss: 0.03731343051832583
updating loss and weight
round 2, starting client 4/90, id: 3
Epoch [1/1], Train Loss: 0.041843109417195413
updating loss and weight
round 2, starting client 5/90, id: 4
Epoch [1/1], Train Loss: 0.04353575510057535
updating loss and weight
round 2, starting client 6/90, id: 5
Epoch [1/1], Train Loss: 0.04080420746468008
updating loss and weight
round 2, starting client 7/90, id: 6
Epoch [1/1], Train Loss: 0.04690153896808625
updating loss and weight
round 2, starting client 8/90, id: 7
Epoch [1/1], Train Loss: 0.037172590329680795
updating loss and weight
round 2, starting client 9/90, id: 8
Epoch [1/1], Train Loss: 0.04402498664477697
updating loss and weight
round 2, starting client 10/90, id: 9
Epoch [1/1], Train Loss: 0.0350353

...

Epoch [1/1], Train Loss: 0.002205094583947563
round 96, starting client 2/90, id: 1
Epoch [1/1], Train Loss: 0.0019960788783565577
round 96, starting client 3/90, id: 2
Epoch [1/1], Train Loss: 0.0021622689447313966
round 96, starting client 4/90, id: 3
Epoch [1/1], Train Loss: 0.002449837421961859
round 96, starting client 5/90, id: 4
Epoch [1/1], Train Loss: 0.0021249199847013438
round 96, starting client 6/90, id: 5
Epoch [1/1], Train Loss: 0.0021008746887673626
round 96, starting client 7/90, id: 6
Epoch [1/1], Train Loss: 0.002023631285221593
round 96, starting client 8/90, id: 7
Epoch [1/1], Train Loss: 0.0016163262178383344
round 96, starting client 9/90, id: 8
Epoch [1/1], Train Loss: 0.0027322745613323957
round 96, starting client 10/90, id: 9
Epoch [1/1], Train Loss: 0.001976527293057491
round 96, starting client 11/90, id: 10
Epoch [1/1], Train Loss: 0.0022633909356954973
round 96, starting client 12/90, id: 11
Epoch [1/1], Train Loss: 0.0020630564433399977
round 96, startin

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0019179165219440006
round 97, starting client 2/90, id: 1
Epoch [1/1], Train Loss: 0.001976515614013705
round 97, starting client 3/90, id: 2
Epoch [1/1], Train Loss: 0.0022511805873364214
round 97, starting client 4/90, id: 3
Epoch [1/1], Train Loss: 0.0024011375373411996
round 97, starting client 5/90, id: 4
Epoch [1/1], Train Loss: 0.002126066815848886
round 97, starting client 6/90, id: 5
Epoch [1/1], Train Loss: 0.0020893299326417035
round 97, starting client 7/90, id: 6
Epoch [1/1], Train Loss: 0.001991984890648038
round 97, starting client 8/90, id: 7
Epoch [1/1], Train Loss: 0.0015027624640596216
round 97, starting client 9/90, id: 8
Epoch [1/1], Train Loss: 0.002675250188286345
round 97, starting client 10/90, id: 9
Epoch [1/1], Train Loss: 0.0019688907920714918
round 97, starting client 11/90, id: 10
Epoch [1/1], Train Loss: 0.0022569529852868673
round 97, starting client 12/90, id: 11
Epoch [1/1], Train Loss: 0.0020576425518619977
round 97, startin

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.00191231558367364
updating loss and weight
round 98, starting client 2/90, id: 1
Epoch [1/1], Train Loss: 0.001968992919298924
updating loss and weight
round 98, starting client 3/90, id: 2
Epoch [1/1], Train Loss: 0.0022451556805107332
updating loss and weight
round 98, starting client 4/90, id: 3
Epoch [1/1], Train Loss: 0.0023933111349869448
updating loss and weight
round 98, starting client 5/90, id: 4
Epoch [1/1], Train Loss: 0.002117893105605617
updating loss and weight
round 98, starting client 6/90, id: 5
Epoch [1/1], Train Loss: 0.0020810937086935158
updating loss and weight
round 98, starting client 7/90, id: 6
Epoch [1/1], Train Loss: 0.0019851476740645807
updating loss and weight
round 98, starting client 8/90, id: 7
Epoch [1/1], Train Loss: 0.001499250009524162
updating loss and weight
round 98, starting client 9/90, id: 8
Epoch [1/1], Train Loss: 0.002665563145106157
updating loss and weight
round 98, starting client 10/90, id: 9
Epoch [1/1], Tr

In [27]:
loss_lbskd = np.insert(loss_lbskd, 0, loss_lbskd1)
smape_lbskd = np.insert(smape_lbskd, 0, smape_lbskd1)
mae_lbskd = np.insert(mae_lbskd, 0, mae_lbskd1)
rmse_lbskd = np.insert(mae_lbskd, 0, mae_lbskd1)

In [28]:
np.save(f'metrics/fedlbskd_outputs_C{n_clients}.npy', np.array(outputs_lbskd, dtype=object))
np.save(f'metrics/fedlbskd_targets_C{n_clients}.npy', np.array(targets_lbskd, dtype=object))
np.save(f'metrics/fedlbskd_loss_C{n_clients}.npy', loss_lbskd)
np.save(f'metrics/fedlbskd_smape_C{n_clients}.npy', smape_lbskd)
np.save(f'metrics/fedlbskd_mae_C{n_clients}.npy', mae_lbskd)
np.save(f'metrics/fedlbskd_rmse_C{n_clients}.npy', rmse_lbskd)